# Master Table Constructor

The code in this section creates the data for the San Francisco Planning Department's Neighborhood Profiles Interactive Tool. The Neighborhood Profiles Interactive Tool (SFNP) provides data and information about communities in the city, including socio-economic profiles derived from American Community Survey to list of community organizations and planning projects in different areas in San Francisco. This notebook creates a master data table that contains every data point required by SFNP. The code is based off methods created by Michael Webster, Jason Sherba, and others. Run the notebook to:

- Download ACS data using the Census API
- Calculate socio-economic summary data by geographies (Analysis Neighborood, Census Tract), by race/ethnicity groups from the lastest ACS 5 years and some past surveys. 
- Integrate non-ACS data regarding community organizations and planning efforts to the ACS summary data. 
- Export the final data as a csv file. 

## Import packages

In [60]:
import numpy as np
np.__version__
np.__path__
import sys
sys.version_info

sys.version_info(major=3, minor=9, micro=13, releaselevel='final', serial=0)

In [61]:
import requests, json, os
import pandas as pd
import numpy as np
import geopandas as gpd
import sodapy
from sodapy import Socrata
from collections import defaultdict
from collections import OrderedDict
from arcgis.gis import GIS

# Part 1. ACS 5-year data

The code in this section creates the socio-economic profile data for Analysis Neighborhoods and census tracts in SF. The data is derived from the [American Community Survey](https://www.census.gov/programs-surveys/acs) 5-year data and consists of four groups of data which includes: 

- Data of Total Population (current year)
    - Language Spoken Data (Detailed)
- Data of Race/Ethnicity Groups (current year) 

- Data of Total Population (10 years prior to current year)
- Data of Race/Ethnicity Groups (10 years prior to current year)

## Set analysis year

Set the years below following the instruction

In [16]:
year = 2020 # the current year 
year_past = 2010 # 10 years past to the current year 
year_language= 2015 # the latest year in which the detailed language spoken data was available. 

## Retrieve data from Census API
All socio-economic data comes from the Census ACS 5-year estimates and is available at the tract level through the census API. API documentation and data for the 2020 ACS data and previous years is available [here](https://www.census.gov/data/developers/data-sets/acs-5year.html)

### Census Attribute IDs
The census API returns ACS attribute vales for provided attribute IDs. A list of relevant attribute ID's needed for calculating the socio-economic profile data is compiled below from IDs stored in a series of csv files named as attribute lookup tables. Below is the pairs of data and lookup tables needed to compile the data:

- Data of Total Population (current year): [attribute_lookup.csv](https://github.com/jsherba/socio-economic-profiles/blob/main/lookup_tables/attribute_lookup.csv)
    - Language Spoken Data (Detailed): [language_attribute_lookup.csv](https://github.com/jsherba/socio-economic-profiles/blob/main/lookup_tables/language_attribute_lookup.csv) 
- Data of Race/Ethnicity Groups (current year): [race_attribute_lookup.csv](https://github.com/jsherba/socio-economic-profiles/blob/main/lookup_tables/language_attribute_lookup.csv) 
- Data of Total Population (10 years prior to current year): [attribute_lookup_past.csv](https://github.com/jsherba/socio-economic-profiles/blob/main/lookup_tables/language_attribute_lookup.csv) 
- Data of Race/Ethnicity Groups (10 years prior to current year): [race_attribute_lookup_past.csv](https://github.com/jsherba/socio-economic-profiles/blob/main/lookup_tables/language_attribute_lookup.csv) 

For a full list of ACS attribute IDs and their meanings visit the API docs [here](https://api.census.gov/data/2019/acs/acs5/variables.html).

In [17]:
# Total Population
# Create list of attribute IDs from attribute_lookup.csv

attribute_lookup_df = pd.read_csv (r'./lookup_tables/attribute_lookup.csv', dtype=str)

attribute_ids_extracted = attribute_lookup_df['attribute_id'].tolist()
attribute_ids = []
for attribute_id in attribute_ids_extracted:
    attribute_ids.extend(attribute_id.split(", "))
attribute_ids = list(set([x+"E" for x in attribute_ids]))
print(len(attribute_ids))
attribute_ids[:10]

363


['B15003_025E',
 'B19101_012E',
 'B16007_011E',
 'B25004_002E',
 'B19001_004E',
 'B15003_017E',
 'B01001_041E',
 'B25070_004E',
 'B25014_005E',
 'B25046_001E']

In [18]:
# Language Spoken (Detailed)
# Create list of attribute IDs from language_attribute_lookup.csv

language_attribute_lookup_df = pd.read_csv (r'./lookup_tables/language_attribute_lookup.csv', dtype=str)

language_attribute_ids_extracted = language_attribute_lookup_df['attribute_id'].tolist()
language_attribute_ids = []
for language_attribute_id in language_attribute_ids_extracted:
    language_attribute_ids.extend(language_attribute_id.split(", "))
language_attribute_ids = list(set([x+"E" for x in language_attribute_ids]))
print(len(language_attribute_ids))
language_attribute_ids[:10]

33


['B16001_003E',
 'B16001_078E',
 'B16001_011E',
 'B16001_083E',
 'B16001_099E',
 'B16001_086E',
 'B16001_105E',
 'B16001_081E',
 'B16001_009E',
 'B16001_006E']

In [19]:
# Race/Ethnicity Groups
# Create list of attribute IDs from language_attribute_lookup.csv

race_attribute_lookup_df = pd.read_csv(r'./lookup_tables/race_attribute_lookup.csv', dtype=str)

race_attribute_ids_extracted = race_attribute_lookup_df['attribute_id'].tolist()
race_attribute_ids = []
for race_attribute_id in race_attribute_ids_extracted:
    race_attribute_ids.extend(race_attribute_id.split(", "))
race_attribute_ids = list(set([x+"E" for x in race_attribute_ids]))
print(len(race_attribute_ids))
race_attribute_ids[:10]

635


['B01001C_001E',
 'B07004D_001E',
 'C23002B_004E',
 'B18101C_003E',
 'B01001D_022E',
 'C15002A_010E',
 'C15002H_005E',
 'B18101I_009E',
 'B19001D_006E',
 'B19001A_001E']

### Build Census API URL and Make Query
The code below builds the URL for the census API call to get relevant ACS attribute data at the tract level for San Francisco County. The Census API accepts up to 50 attributes at a time. Therefore the attribute list is first grouped into sublists of 45 attribute IDs. An API call is. Below define:
- Tract code is '*' to collect all tracts
- State code is '06' for CA
- County code is '075' for San Francisco County
- Attributes are defined by the attribute id list and includes all relevant attributes for the socio-economic data calcs

#### Set up functions for API call

In [20]:
# function builds the api URL from tract_code, state_code, county_code, and attribute ids. 
def build_census_url(tract_code, state_code, county_code, attribute_ids, year):
    attributes = ','.join(attribute_ids)
    census_url = r'https://api.census.gov/data/{}/acs/acs5?get={}&for=tract:{}&in=state:{}&in=county:{}'\
                .format(year, attributes, tract_code, state_code, county_code)
    return census_url
    

In [21]:
# function makes a single api call and collects results in a pandas dataframe
def make_census_api_call(census_url):
    # make API call to Census
    resp = requests.get(census_url)
    if resp.status_code != 200:
        # this means something went wrong
        resp.raise_for_status()
       
    # retrieve data as json and convert to Pandas Dataframe
    data = resp.json()
    headers = data.pop(0)
    df = pd.DataFrame(data, columns=headers)

    # convert values that are not state, county, or tract to numeric type
    cols=[i for i in df.columns if i not in ["state","county","tract"]]
    for col in cols:
        #print('col is:', df[col])
        #print(type(df[col]))
        df[col]=pd.to_numeric(df[col])
        
    return df

#### Set geo variables for api call

In [22]:
tract_code = "*"
state_code = "06"
county_code = "075"

#### Compile data: Total Population

In [47]:
# split attributes into groups of 45, run a census query for each, merge outputs into a single df
split_attribute_ids = [attribute_ids[i:i+45] for i in range(0, len(attribute_ids), 45)]
df=None
first = True
for ids in split_attribute_ids:
    census_url = build_census_url(tract_code, state_code, county_code, ids, year)
    returned_df = make_census_api_call(census_url)
    if first:
        df = returned_df
        first = False
    else:
        returned_df = returned_df.drop(columns=['state', 'county'])
        df = pd.merge(df, returned_df, on='tract', how='left')

df.head()

B15003_025E  B19101_012E  B16007_011E  B25004_002E  B19001_004E  \
0           26           45          105            0          124   
1           22            0           26            0           33   
2           60            0          120          107           13   
3           60           33            0            0            0   
4           96          129           98            0           23   

   B15003_017E  B01001_041E  B25070_004E  B25014_005E  B25046_001E  ...  \
0          208           86          125            0        642.0  ...   
1          122           50           62            0        809.0  ...   
2           30           96          273            0       1035.0  ...   
3           23           19          133            0       1272.0  ...   
4          309           95          413            0       1871.0  ...   

   B16003_006E  B06007_004E  B25024_011E  B25014_007E  B25063_010E  \
0           47           14            0            0            0   
1           12          146            0            0            0   
2            0           15            0            0            0   
3            0           18            0            0            0   
4           15           77            0            0            0   

   B25075_003E  B25074_043E  B23001_097E  B18101_032E  B23001_165E  
0            0           15            0          115            0  
1            0            0            0          184            0  
2            0           34            0           16           37  
3            0            0            0            1           12  
4            0           65            0           37           14  

[5 rows x 366 columns]

#### Compile data: Language Spoken

In [48]:
# language: run a census query for each, merge outputs into a single df
split_language_attribute_ids = [language_attribute_ids[i:i+45] for i in range(0, len(language_attribute_ids), 45)]

first = False
for ids in split_language_attribute_ids:
    census_url = build_census_url(tract_code, state_code, county_code, ids, year_language)
    #print(census_url)
    returned_df = make_census_api_call(census_url)
    if first:
        df = returned_df
        first = False
    else:
        returned_df = returned_df.drop(columns=['state', 'county'])
        df = pd.merge(df, returned_df, on='tract', how='left')

df.head()

B15003_025E  B19101_012E  B16007_011E  B25004_002E  B19001_004E  \
0           26           45          105            0          124   
1           22            0           26            0           33   
2           60            0          120          107           13   
3           60           33            0            0            0   
4           96          129           98            0           23   

   B15003_017E  B01001_041E  B25070_004E  B25014_005E  B25046_001E  ...  \
0          208           86          125            0        642.0  ...   
1          122           50           62            0        809.0  ...   
2           30           96          273            0       1035.0  ...   
3           23           19          133            0       1272.0  ...   
4          309           95          413            0       1871.0  ...   

   B16001_018E  B16001_050E  B16001_020E  B16001_001E  B16001_056E  \
0          NaN          NaN          NaN          NaN          NaN   
1          NaN          NaN          NaN          NaN          NaN   
2          NaN          NaN          NaN          NaN          NaN   
3          NaN          NaN          NaN          NaN          NaN   
4         27.0          0.0          0.0       4143.0          0.0   

   B16001_077E  B16001_057E  B16001_027E  B16001_014E  B16001_005E  
0          NaN          NaN          NaN          NaN          NaN  
1          NaN          NaN          NaN          NaN          NaN  
2          NaN          NaN          NaN          NaN          NaN  
3          NaN          NaN          NaN          NaN          NaN  
4          0.0          0.0          0.0         37.0          0.0  

[5 rows x 399 columns]

#### Compile data: Race/Ethnicity Groups

In [49]:
# race/ethnicity: run a census query for each, merge outputs into a single df
# if a call returns 'Bad Request for url', 
# click the url in the error message, look up the 'unknown variable' in the attribute lookups 
split_race_attribute_ids = [race_attribute_ids[i:i+45] for i in range(0, len(race_attribute_ids), 45)]

first = False
for ids in split_race_attribute_ids:
    census_url = build_census_url(tract_code, state_code, county_code, ids, year)
    #print(census_url)
    returned_df = make_census_api_call(census_url)
    if first:
        df = returned_df
        first = False
    else:
        returned_df = returned_df.drop(columns=['state', 'county'])
        df = pd.merge(df, returned_df, on='tract', how='left')

df.head()

B15003_025E  B19101_012E  B16007_011E  B25004_002E  B19001_004E  \
0           26           45          105            0          124   
1           22            0           26            0           33   
2           60            0          120          107           13   
3           60           33            0            0            0   
4           96          129           98            0           23   

   B15003_017E  B01001_041E  B25070_004E  B25014_005E  B25046_001E  ...  \
0          208           86          125            0        642.0  ...   
1          122           50           62            0        809.0  ...   
2           30           96          273            0       1035.0  ...   
3           23           19          133            0       1272.0  ...   
4          309           95          413            0       1871.0  ...   

   B19001H_014E  B18101B_009E  B26103C_002E  B19101C_016E  B19001C_011E  \
0            87             0           NaN             0             0   
1            23             0           NaN             0             0   
2           104             0           NaN             0             0   
3            46             0           NaN             0             0   
4            66             0           NaN            11             0   

   C15002H_009E  B19101H_015E  B01001C_022E  B19001C_017E  B19101I_008E  
0             6             0             0             0             0  
1            12             0             0             0             0  
2            16            76             0             0             0  
3            10            30             0             0             0  
4            56            13             0             0             0  

[5 rows x 1034 columns]

In [102]:
df[['B01001_001E', 'tract']]#[df['tract']=='060700']

B01001_001E   tract
0           2045  010101
1           1920  010102
2           2331  010201
3           1984  010202
4           4282  010300
..           ...     ...
239          153  980501
240          747  980600
241          242  980900
242            0  990100
243            0  990200

[244 rows x 2 columns]

## Prepare Lookup Dictionaries and Helper Functions

### Tract/Neighborhood Lookup
A lookup dictionaries are created below that relates neghborhoods to tracts. The dictionary is used to subset the census dataframe for each neighborhood so that calcs can be run on each set of tracts. The lookup dictionary is created from [geo_lookup.csv]() in the repository.

In [107]:
# import geo_lookup csv
geo_lookup_df = pd.read_csv (r'./lookup_tables/geo_lookup_2020.csv', dtype=str)

tract_tr_lookup = defaultdict(list)
tract_nb_lookup = defaultdict(list)
tract_sd_lookup = defaultdict(list)
all_tracts = list(set(df['tract'].tolist()))
# create tract lookup dictionary for tracts 
for i in all_tracts:
    tract_tr_lookup[i].append(i)
# create tract lookup dictionary for neighborhoods
for i, j in zip(geo_lookup_df['neighborhood'], geo_lookup_df['tractid']):
    tract_nb_lookup[i].append(j)
tract_nb_lookup["sf"]= all_tracts
    
first_4 = list(tract_nb_lookup.items())


In [110]:
geo_lookup_df

tractid           neighborhood supervisor_district           city
0    010101            North Beach                   3  San Francisco
1    010102            North Beach                   3  San Francisco
2    010201           Russian Hill                   2  San Francisco
3    010202           Russian Hill                   2  San Francisco
4    010300           Russian Hill                   3  San Francisco
..      ...                    ...                 ...            ...
236  980200           Lincoln Park                   1  San Francisco
237  980300       Golden Gate Park                   1  San Francisco
238  980501           McLaren Park                  10  San Francisco
239  980600  Bayview Hunters Point                  10  San Francisco
240  980900  Bayview Hunters Point                  10  San Francisco

[241 rows x 4 columns]

### Calculating Medians
To calculate median values of aggregated geographies you cannot use the mean of component geographies. Instead a statistical approximation of the median must be calculated from range tables. 

Range variables in the ACS have a unique ID like any other Census variable. They represent the amount of a variable within a select range. e.g. number of households with household incomes between $45000-50000. 

Range variable ID's and range information is stored in the [median_ranges.csv]() file and [median_ranges_race.csv]() in the repository. These range variables and ranges are needed for calculating the median at the neighborhood level. 

The below function calculates a median based on range data. This method follows the offical ACS documentation for [calculating a median](https://www.dof.ca.gov/Forecasting/Demographics/Census_Data_Center_Network/documents/How_to_Recalculate_a_Median.pdf)


#### Medians for Total Population

In [28]:
#all population: import median tables from median_ranges csv and add empty columns for rows 'households and 'cumulative_totals'
range_all_df = pd.read_csv (r'./lookup_tables/median_ranges.csv')
range_all_df['households']=0
range_all_df['cumulative_total']=0
range_all_df.head()

name           id  range_start  range_end  households  \
0  median_household_income  B19001_002E       2500.0     9999.0           0   
1  median_household_income  B19001_003E      10000.0    14999.0           0   
2  median_household_income  B19001_004E      15000.0    19999.0           0   
3  median_household_income  B19001_005E      20000.0    24999.0           0   
4  median_household_income  B19001_006E      25000.0    29999.0           0   

   cumulative_total  
0                 0  
1                 0  
2                 0  
3                 0  
4                 0

#### Medians for Race/Ethnicity groups

In [29]:
#race/ethnicity: import median tables from median_ranges_race csv and add empty columns for rows 'households and 'cumulative_totals'
range_race_df = pd.read_csv (r'./lookup_tables/median_ranges_race.csv')
range_race_df['households']=0
range_race_df['cumulative_total']=0
range_race_df.head()

name            id  range_start  range_end  \
0  A_median_household_income  B19001A_002E         2500       9999   
1  A_median_household_income  B19001A_003E        10000      14999   
2  A_median_household_income  B19001A_004E        15000      19999   
3  A_median_household_income  B19001A_005E        20000      24999   
4  A_median_household_income  B19001A_006E        25000      29999   

   households  cumulative_total  
0           0                 0  
1           0                 0  
2           0                 0  
3           0                 0  
4           0                 0

#### Define Median Helper Function

In [30]:
# define median helper function
def calc_median(tract_df, range_df, median_to_calc):
    
    # subset range df for current median variable to calc
    range_df = range_df[range_df['name']==median_to_calc]
    print(range_df)
    
    # sort dataframe low to high by range start column
    range_df = range_df.sort_values(by=['range_start'])
    
    # calculate households as sum of tract level households for each row based on range id
    range_df['households'] = range_df.apply(lambda row : tract_df[row['id']].sum(), axis = 1)
    
    # calculate the cumulative total of households
    range_df['cumulative_total'] = range_df['households'].cumsum()
    
    # calculate total households and return 0 if total households is 0
    total_households = range_df['households'].sum()
    
    # if total households is 0 set median to 0
    if total_households == 0:
        return 0
    
    # calculate midpoint
    midpoint = total_households/2

    # if midpoint is below first range return median as end of first range value
    if midpoint < range_df['cumulative_total'].min():
        new_median = range_df['range_end'].min()
        return new_median
    
    # if midpoint is above last range set median to end of last range value
    if midpoint > range_df['cumulative_total'].max():
        new_median = range_df['range_end'].max()
        return new_median
    
    less_midpoint_df = range_df[range_df['cumulative_total']<midpoint]
    
    # get the single row containing the range just below the mid range by getting the row with the max range start from the subsetted median df
    range_below_mid_range_df = less_midpoint_df[less_midpoint_df['range_start'] == less_midpoint_df['range_start'].max()]
    
    # get the cumulative total value for the first row of the range below mid range dictionary
    total_hh_previous_range = range_below_mid_range_df['cumulative_total'].iloc[0]
    hh_to_mid_range = midpoint - total_hh_previous_range
    
    # extract rows above midrange by subsetting median df for rows with cumulative total grearter than midpoint.
    greater_midpoint_df = range_df[range_df['cumulative_total']>midpoint]
    
    # get the single row containing the mid range by getting the row with the min range start from the subsetted median df
    mid_range_df = greater_midpoint_df[greater_midpoint_df['range_start'] == greater_midpoint_df['range_start'].min()]
    
    # get the households value for the first row of the mid range dictionary
    hh_in_mid_range = mid_range_df['households'].iloc[0]
    
    # calculate proportion of number of households in the mid range that would be needed to get to the mid-point
    prop_of_hh = hh_to_mid_range/hh_in_mid_range
    
    # calculate width of the mid range
    width = (mid_range_df['range_end'].iloc[0]-mid_range_df['range_start'].iloc[0])+1
    
    # apply proportion to width of mid range
    prop_to_width = prop_of_hh*width
    beginning_of_mid_range = mid_range_df['range_start'].iloc[0]
    
    # calculate new median
    new_median = beginning_of_mid_range + prop_to_width
    
    return new_median

## Define functions for calculating socio-economic data


The `calc_socio_economic_data` function family takes tract level data from the API call and the tract/neighborhood lookup dictionary. These functions create all of the socio-economic data calcs and returns a dictionary. The calcs in this function are derived from the [Data_Items_and_Sources.xlsx](https://github.com/jsherba/socio-economic-profiles/raw/main/Data_Items_And_Sources_2019.xlsx). 

### Calculation helper functions
- `calc_sum(df, attribute_id)`: sum values of all given attributes
- `calc_normalized(df, attribute_id, attribute_id2)`: normalized the 1st attribute value with the 2nd attribute value 
- `calc_sum_normalized(df, attribute_list, attribute_id2)`: normalized the sum of the attribute values (attribute list) by the 2nd attribute value  

In [31]:
# define calculation helper functions
def calc_sum(df, attribute_id):
    return df[attribute_id].sum()

def calc_normalized(df, attribute_id, attribute_id2):
    if df[attribute_id2].sum() == 0:
        return 0
    else:
        return (df[attribute_id].sum()/df[attribute_id2].sum())

def calc_sum_normalized(df, attribute_list, attribute_id2):
    if df[attribute_id2].sum()==0:
        return 0
    else:
        sum_of_attributes = 0
        for attribute_id in attribute_list:
            sum_of_attributes+=df[attribute_id].sum()
        return sum_of_attributes/df[attribute_id2].sum()
    

### Attribute value calculation function

In [32]:
# function runs all calcs for each neighborhood or census tracts
def calc_socio_economic_data(df, lookup_df, range_df, tract_lookup):

    all_calc_data = defaultdict(dict) 
    attribute_ids_extracted = lookup_df['attribute_id'].tolist()
    attribute_names = lookup_df['attribute_name'].tolist()
    calc_types = lookup_df['calc_type'].tolist()
    median_calc_types = lookup_df['median_type'].tolist()


    for nb_name, tracts in tract_lookup.items():
        # extract attribute information for tracks associated with a neighborhood
        tract_df = df[df['tract'].isin(tracts)]
        print(len(tract_df))
        # build dictionary with all stats for a neighborhood
        all_calc_data_nb = all_calc_data[nb_name]

        for i in range(0, len(lookup_df)):
            name = attribute_names[i]
            calc = calc_types[i]
            print(attribute_ids_extracted[i])
            attribute_ids = attribute_ids_extracted[i].split(", ")
            attribute_ids = [x+"E" for x in attribute_ids]

            if calc == 'sum':
                new_dict = {name:calc_sum(tract_df, attribute_ids[0])}
                all_calc_data_nb.update(new_dict) 
            elif calc == 'sum_normalized':
                new_dict = {name:calc_sum_normalized(tract_df, attribute_ids[:-1], attribute_ids[-1])}
                all_calc_data_nb.update(new_dict) 
            elif calc == 'normalized':
                new_dict = {name:calc_normalized(tract_df, attribute_ids[0], attribute_ids[1])}
                print(attribute_ids[0], attribute_ids[1])
                all_calc_data_nb.update(new_dict) 
            elif calc == 'median':
                median_calc = median_calc_types[i]
                new_dict = {name:calc_median(tract_df, range_df, median_calc)}
                all_calc_data_nb.update(new_dict) 
            elif calc == 'none':
                new_dict = {name:np.nan}
                all_calc_data_nb.update(new_dict) 

    return all_calc_data

## Caculate Socioeconomic Profiles

### Set Summary Variables (Neighborhood or Census Tract) and Output Paths

Now you are ready to calculate attribute values summarized at a geographic level of your selection. Set `geo_summary_variable` below as `Neighborhood` first and run the following codes. After exporting the final data table as a csv file, come back here, set the `geo_summary_variable` as `Tract` and repeat running the code until you reach the final exporting stage again.  

In [104]:
# set path to download csvs
download_path = r"./output"

In [105]:
# set geography to summarize by. If supervisor districts set geo_summary_variable to "Superisor District"
geo_summary_variable = 'Neighborhood'#'Tract'

# sets geo variables based on above choice
if geo_summary_variable == 'Tract':
    tract_lookup = tract_tr_lookup
    geo_path = r'./shps/tracts_2020/tracts_sf.shp'
    geo_merge_variable = 'tractce'
elif geo_summary_variable == 'Neighborhood':
    tract_lookup = tract_nb_lookup
    geo_path = r'./shps/neighborhoods/neighborhoods5/neighborhoods5.shp'
    geo_merge_variable = 'nhood'

### Run Socioeconomic Profiles Calcs

#### Total Population

In [53]:
# run functions to calculate all stats and convert calc dictionary to pandas dataframe
all_calc_data = calc_socio_economic_data(df, attribute_lookup_df, range_all_df, tract_lookup)
print(len(all_calc_data))
df_all_calcs = pd.DataFrame.from_dict(all_calc_data).reset_index()
df_all_calcs.rename(columns = {'index':'Attribute'}, inplace = True) 
print(len(df_all_calcs))
df_all_calcs.head()


5
B01001_001
B26001_001
B01001_026
B18101_004, B18101_007, B18101_010, B18101_013, B18101_016, B18101_019, B18101_023, B18101_026, B18101_029, B18101_032, B18101_035, B18101_038, B18101_001
B11001_001
B11001_002, B11001_001
B11001_002E B11001_001E
B11001_007, B11001_001
B11001_007E B11001_001E
B11001_008, B11001_001
B11001_008E B11001_001E
B11005_002, B11001_001
B11005_002E B11001_001E
B11006_002, B11001_001
B11006_002E B11001_001E
B11007_003, B11007_001
B11007_003E B11007_001E
B11002_001, B11001_001
B11002_001E B11001_001E
B11002_002, B11001_002
B11002_002E B11001_002E
B02001_005, B02001_001
B02001_005E B02001_001E
B02001_003, B02001_001
B02001_003E B02001_001E
B02001_002, B02001_001
B02001_002E B02001_001E
B02010_001, B02001_001
B02010_001E B02001_001E
B02001_006, B02001_001
B02001_006E B02001_001E
B02001_008, B02001_007, B02001_001
B03001_003, B03001_001
B03001_003E B03001_001E
B01001_003, B01001_027, B01001_001
B01001_004, B01001_005, B01001_006, B01001_028, B01001_029, B01001_030,

B25004_004E B25004_001E
B25004_003, B25004_005, B25004_001
B25004_006, B25004_001
B25004_006E B25004_001E
B25004_008, B25004_001
B25004_008E B25004_001E
B07001_017, B07001_001
B07001_017E B07001_001E
B07001_017
B07001_001
B25014_005, B25014_006, B25014_007, B25014_011, B25014_012, B25014_013, B25014_001
B25024_002, B25024_003, B25024_001
B25024_004, B25024_005, B25024_001
B25024_006, B25024_001
B25024_006E B25024_001E
B25024_007, B25024_001
B25024_007E B25024_001E
B25024_008, B25024_009, B25024_001
B25024_010, B25024_011, B25024_001
B25041_002, B25041_001
B25041_003, B25041_001
B25041_004, B25041_001
B25041_005, B25041_001
B25041_006, B25041_001
B25041_007, B25041_001
B25063_003, B25063_004, B25063_005, B25063_006, B25063_007, B25063_008, B25063_009, B25063_010, B25063_011, B25063_012, B25063_013, B25063_014, B25063_015, B25063_016, B25063_017, B25063_018, B25063_019, B25063_020, B25063_021, B25063_022, B25063_023, B25063_024, B25063_025, B25063_026
           name           id  range_

B25041_002, B25041_001
B25041_003, B25041_001
B25041_004, B25041_001
B25041_005, B25041_001
B25041_006, B25041_001
B25041_007, B25041_001
B25063_003, B25063_004, B25063_005, B25063_006, B25063_007, B25063_008, B25063_009, B25063_010, B25063_011, B25063_012, B25063_013, B25063_014, B25063_015, B25063_016, B25063_017, B25063_018, B25063_019, B25063_020, B25063_021, B25063_022, B25063_023, B25063_024, B25063_025, B25063_026
           name           id  range_start  range_end  households  \
54  median_rent  B25063_003E         99.0       99.0           0   
55  median_rent  B25063_004E        100.0      149.0           0   
56  median_rent  B25063_005E        150.0      199.0           0   
57  median_rent  B25063_006E        200.0      249.0           0   
58  median_rent  B25063_007E        250.0      299.0           0   
59  median_rent  B25063_008E        300.0      349.0           0   
60  median_rent  B25063_009E        350.0      399.0           0   
61  median_rent  B25063_010E   

B25074_006, B25074_007, B25074_008, B25074_009, B25074_015, B25074_016, B25074_017, B25074_018, B25074_024, B25074_025, B25074_026, B25074_027, B25074_033, B25074_034, B25074_035, B25074_036, B25074_042, B25074_043, B25074_044, B25074_045, B25074_051, B25074_052, B25074_053, B25074_054, B25074_060, B25074_061, B25074_062, B25074_064, B25074_001
B25046_001
B25046_002, B25046_001
B25046_002E B25046_001E
B25046_003, B25046_001
B25046_003E B25046_001E
B25046_001, B01001_001
B25046_001E B01001_001E
B25044_003, B25044_010, B25044_001
B25044_003, B25044_002
B25044_003E B25044_002E
B25044_010, B25044_009
B25044_010E B25044_009E
B19013_001
B19113_001
B19001_002, B19001_003, B19001_004, B19001_005, B19001_006, B19001_007, B19001_008, B19001_009, B19001_010, B19001_011, B19001_012, B19001_013, B19001_014, B19001_015, B19001_016, B19001_017
                       name           id  range_start  range_end  households  \
0   median_household_income  B19001_002E       2500.0     9999.0           0   

B25074_006, B25074_007, B25074_008, B25074_009, B25074_015, B25074_016, B25074_017, B25074_018, B25074_024, B25074_025, B25074_026, B25074_027, B25074_033, B25074_034, B25074_035, B25074_036, B25074_042, B25074_043, B25074_044, B25074_045, B25074_051, B25074_052, B25074_053, B25074_054, B25074_060, B25074_061, B25074_062, B25074_064, B25074_001
B25046_001
B25046_002, B25046_001
B25046_002E B25046_001E
B25046_003, B25046_001
B25046_003E B25046_001E
B25046_001, B01001_001
B25046_001E B01001_001E
B25044_003, B25044_010, B25044_001
B25044_003, B25044_002
B25044_003E B25044_002E
B25044_010, B25044_009
B25044_010E B25044_009E
B19013_001
B19113_001
B19001_002, B19001_003, B19001_004, B19001_005, B19001_006, B19001_007, B19001_008, B19001_009, B19001_010, B19001_011, B19001_012, B19001_013, B19001_014, B19001_015, B19001_016, B19001_017
                       name           id  range_start  range_end  households  \
0   median_household_income  B19001_002E       2500.0     9999.0           0   

B25007_002, B25007_012
B25007_002, B25007_001
B25007_002E B25007_001E
B25007_012, B25007_001
B25007_012E B25007_001E
B25004_001, B25001_001
B25004_001E B25001_001E
B25004_002, B25004_001
B25004_002E B25004_001E
B25004_004, B25004_001
B25004_004E B25004_001E
B25004_003, B25004_005, B25004_001
B25004_006, B25004_001
B25004_006E B25004_001E
B25004_008, B25004_001
B25004_008E B25004_001E
B07001_017, B07001_001
B07001_017E B07001_001E
B07001_017
B07001_001
B25014_005, B25014_006, B25014_007, B25014_011, B25014_012, B25014_013, B25014_001
B25024_002, B25024_003, B25024_001
B25024_004, B25024_005, B25024_001
B25024_006, B25024_001
B25024_006E B25024_001E
B25024_007, B25024_001
B25024_007E B25024_001E
B25024_008, B25024_009, B25024_001
B25024_010, B25024_011, B25024_001
B25041_002, B25041_001
B25041_003, B25041_001
B25041_004, B25041_001
B25041_005, B25041_001
B25041_006, B25041_001
B25041_007, B25041_001
B25063_003, B25063_004, B25063_005, B25063_006, B25063_007, B25063_008, B25063_009, B2506

Attribute   North Beach  Russian Hill  \
0                Total Population  11934.000000  18237.000000   
1        Group Quarter Population     17.000000      5.000000   
2               Female Population   5761.000000   9679.000000   
3  % Population with a Disability      0.145215      0.077315   
4                       Housholds   6308.000000   9601.000000   

   Financial District     Chinatown      Nob Hill    Tenderloin        Marina  \
0        22963.000000  14310.000000  26247.000000  29726.000000  25186.000000   
1          581.000000     55.000000    891.000000   1544.000000     98.000000   
2        10358.000000   7414.000000  12549.000000  13185.000000  13186.000000   
3            0.057092      0.162124      0.089381      0.246546      0.054941   
4        11967.000000   6751.000000  15225.000000  18082.000000  12832.000000   

   Pacific Heights  Presidio Heights  ...     Lakeshore  Inner Richmond  \
0     23953.000000      10445.000000  ...  14368.000000    22753.000000   
1       511.000000        158.000000  ...   2673.000000      161.000000   
2     12078.000000       5384.000000  ...   7591.000000    12463.000000   
3         0.082918          0.075954  ...      0.106695        0.093933   
4     12860.000000       5054.000000  ...   4913.000000     8897.000000   

   Outer Richmond     Seacliff     Presidio   Mission Bay  Lincoln Park  \
0    45745.000000  2416.000000  4073.000000  13330.000000         185.0   
1      191.000000     0.000000     0.000000    321.000000         185.0   
2    24160.000000  1247.000000  2208.000000   6755.000000           0.0   
3        0.110132     0.075745     0.026025      0.078245           0.0   
4    18980.000000   868.000000  1318.000000   6065.000000           0.0   

   Golden Gate Park  McLaren Park             sf  
0              32.0    153.000000  874784.000000  
1               0.0      0.000000   20169.000000  
2               8.0    123.000000  428538.000000  
3               0.0      0.529412       0.101049  
4              25.0    122.000000  362141.000000  

[5 rows x 43 columns]

#### Language Spoken

In [54]:
# run functions to calculate language spoken stats and convert calc dictionary to pandas dataframe
lan_calc_data = calc_socio_economic_data(df, language_attribute_lookup_df, range_all_df, tract_lookup)
df_lan_calcs = pd.DataFrame.from_dict(lan_calc_data).reset_index()
df_lan_calcs.rename(columns = {'index':'Attribute'}, inplace = True) 
print(len(df_lan_calcs))
df_lan_calcs.head()

5
B16001_003, B16001_001
B16001_003E B16001_001E
B16001_005, B16001_001
B16001_005E B16001_001E
B16001_006, B16001_001
B16001_006E B16001_001E
B16001_008, B16001_001
B16001_008E B16001_001E
B16001_009, B16001_001
B16001_009E B16001_001E
B16001_011, B16001_001
B16001_011E B16001_001E
B16001_012, B16001_001
B16001_012E B16001_001E
B16001_014, B16001_001
B16001_014E B16001_001E
B16001_018, B16001_001
B16001_018E B16001_001E
B16001_020, B16001_001
B16001_020E B16001_001E
B16001_027, B16001_001
B16001_027E B16001_001E
B16001_029, B16001_001
B16001_029E B16001_001E
B16001_048, B16001_001
B16001_048E B16001_001E
B16001_050, B16001_001
B16001_050E B16001_001E
B16001_054, B16001_001
B16001_054E B16001_001E
B16001_056, B16001_001
B16001_056E B16001_001E
B16001_057, B16001_001
B16001_057E B16001_001E
B16001_059, B16001_001
B16001_059E B16001_001E
B16001_075, B16001_001
B16001_075E B16001_001E
B16001_077, B16001_001
B16001_077E B16001_001E
B16001_078, B16001_001
B16001_078E B16001_001E
B16001_080,

Attribute  North Beach  Russian Hill  \
0                              Spanish     0.054001      0.035723   
1  Spanish-Limited English proficiency     0.031897      0.000000   
2                               French     0.008114      0.018103   
3   French-Limited English proficiency     0.003917      0.000000   
4                              Haitian     0.000000      0.000000   

   Financial District  Chinatown  Nob Hill  Tenderloin    Marina  \
0            0.050109   0.021133  0.063849    0.175953  0.032119   
1            0.001459   0.004047  0.019063    0.132741  0.004461   
2            0.021892   0.006070  0.018144    0.004916  0.018118   
3            0.005108   0.003372  0.000689    0.002070  0.004530   
4            0.000000   0.000000  0.000000    0.000000  0.000000   

   Pacific Heights  Presidio Heights  ...  Lakeshore  Inner Richmond  \
0         0.050499          0.047826  ...   0.088409        0.045496   
1         0.005242          0.009903  ...   0.015717        0.007246   
2         0.023459          0.018116  ...   0.008916        0.006061   
3         0.000447          0.002899  ...   0.000000        0.001742   
4         0.000000          0.000000  ...   0.000000        0.000000   

   Outer Richmond  Seacliff  Presidio  Mission Bay  Lincoln Park  \
0        0.038415  0.054066  0.056055            0      0.015576   
1        0.013884  0.003460  0.002098            0      0.015576   
2        0.008918  0.012976  0.013189            0      0.000000   
3        0.001043  0.000000  0.000000            0      0.000000   
4        0.000000  0.000000  0.000000            0      0.000000   

   Golden Gate Park  McLaren Park        sf  
0               0.0      0.061684  0.113682  
1               0.0      0.029656  0.046528  
2               0.0      0.000000  0.011862  
3               0.0      0.000000  0.001477  
4               0.0      0.000000  0.000178  

[5 rows x 43 columns]

#### Race/Ethnicity Groups

In [55]:
# run functions to calculate all race/ethnicity stats, convert dictionary to dataframe, append the datafrmae to df_all_calcs
race_calc_data = calc_socio_economic_data(df, race_attribute_lookup_df, range_race_df, tract_lookup)
df_race_calcs = pd.DataFrame.from_dict(race_calc_data).reset_index()
df_race_calcs.rename(columns = {'index':'Attribute'}, inplace = True)
df_race_calcs.head()



5
B01001A_001
B26103A_002
B01001A_017
B18101A_003, B18101A_006, B18101A_009
B06004A_005, B06004A_001
B06004A_005E B06004A_001E
B05003A_006, B05003A_011, B05003A_017, B05003A_022, B05003A_001
B11001A_001
B11001A_002, B11001A_001
B11001A_002E B11001A_001E
B11001A_007, B11001A_001
B11001A_007E B11001A_001E
B11001A_008, B11001A_001
B11001A_008E B11001A_001E
B11002A_001, B11001A_001
B11002A_001E B11001A_001E
B11002A_002, B11001A_002
B11002A_002E B11001A_002E
B01001A_003, B01001A_018, B01001A_001
B01001A_004, B01001A_005, B01001A_006, B01001A_019, B01001A_020, B01001A_021, B01001A_001
B01001A_007, B01001A_008, B01001A_009, B01001A_010, B01001A_022, B01001A_023, B01001A_024, B01001A_025, B01001A_001
B01001A_011, B01001A_012, B01001A_013, B01001A_026, B01001A_027, B01001A_028, B01001A_001
B01001A_014, B01001A_015, B01001A_016, B01001A_029, B01001A_030, B01001A_031, B01001A_001
C15002A_003, C15002A_008, C15002A_001
C15002A_004, C15002A_009, C15002A_001
C15002A_005, C15002A_010, C15002A_001
C150

B19101D_002, B19101D_003, B19101D_004, B19101D_005, B19101D_006, B19101D_007, B19101D_008, B19101D_009, B19101D_010, B19101D_011, B19101D_012, B19101D_013, B19101D_014, B19101D_015, B19101D_016, B19101D_017
                       name            id  range_start  range_end  households  \
112  D_median_family_income  B19101D_002E         2500       9999           0   
113  D_median_family_income  B19101D_003E        10000      14999           0   
114  D_median_family_income  B19101D_004E        15000      19999           0   
115  D_median_family_income  B19101D_005E        20000      24999           0   
116  D_median_family_income  B19101D_006E        25000      29999           0   
117  D_median_family_income  B19101D_007E        30000      34999           0   
118  D_median_family_income  B19101D_008E        35000      39999           0   
119  D_median_family_income  B19101D_009E        40000      44999           0   
120  D_median_family_income  B19101D_010E        45000      4999

B19101C_002, B19101C_003, B19101C_004, B19101C_005, B19101C_006, B19101C_007, B19101C_008, B19101C_009, B19101C_010, B19101C_011, B19101C_012, B19101C_013, B19101C_014, B19101C_015, B19101C_016, B19101C_017
                      name            id  range_start  range_end  households  \
80  C_median_family_income  B19101C_002E         2500       9999           0   
81  C_median_family_income  B19101C_003E        10000      14999           0   
82  C_median_family_income  B19101C_004E        15000      19999           0   
83  C_median_family_income  B19101C_005E        20000      24999           0   
84  C_median_family_income  B19101C_006E        25000      29999           0   
85  C_median_family_income  B19101C_007E        30000      34999           0   
86  C_median_family_income  B19101C_008E        35000      39999           0   
87  C_median_family_income  B19101C_009E        40000      44999           0   
88  C_median_family_income  B19101C_010E        45000      49999         

B19101A_002, B19101A_003, B19101A_004, B19101A_005, B19101A_006, B19101A_007, B19101A_008, B19101A_009, B19101A_010, B19101A_011, B19101A_012, B19101A_013, B19101A_014, B19101A_015, B19101A_016, B19101A_017
                      name            id  range_start  range_end  households  \
16  A_median_family_income  B19101A_002E         2500       9999           0   
17  A_median_family_income  B19101A_003E        10000      14999           0   
18  A_median_family_income  B19101A_004E        15000      19999           0   
19  A_median_family_income  B19101A_005E        20000      24999           0   
20  A_median_family_income  B19101A_006E        25000      29999           0   
21  A_median_family_income  B19101A_007E        30000      34999           0   
22  A_median_family_income  B19101A_008E        35000      39999           0   
23  A_median_family_income  B19101A_009E        40000      44999           0   
24  A_median_family_income  B19101A_010E        45000      49999         

B19001I_002, B19001I_003, B19001I_004, B19001I_005, B19001I_006, B19001I_007, B19001I_008, B19001I_009, B19001I_010, B19001I_011, B19001I_012, B19001I_013, B19001I_014, B19001I_015, B19001I_016, B19001I_017
                          name            id  range_start  range_end  \
160  I_median_household_income  B19001I_002E         2500       9999   
161  I_median_household_income  B19001I_003E        10000      14999   
162  I_median_household_income  B19001I_004E        15000      19999   
163  I_median_household_income  B19001I_005E        20000      24999   
164  I_median_household_income  B19001I_006E        25000      29999   
165  I_median_household_income  B19001I_007E        30000      34999   
166  I_median_household_income  B19001I_008E        35000      39999   
167  I_median_household_income  B19001I_009E        40000      44999   
168  I_median_household_income  B19001I_010E        45000      49999   
169  I_median_household_income  B19001I_011E        50000      59999   
1

5
B01001A_001
B26103A_002
B01001A_017
B18101A_003, B18101A_006, B18101A_009
B06004A_005, B06004A_001
B06004A_005E B06004A_001E
B05003A_006, B05003A_011, B05003A_017, B05003A_022, B05003A_001
B11001A_001
B11001A_002, B11001A_001
B11001A_002E B11001A_001E
B11001A_007, B11001A_001
B11001A_007E B11001A_001E
B11001A_008, B11001A_001
B11001A_008E B11001A_001E
B11002A_001, B11001A_001
B11002A_001E B11001A_001E
B11002A_002, B11001A_002
B11002A_002E B11001A_002E
B01001A_003, B01001A_018, B01001A_001
B01001A_004, B01001A_005, B01001A_006, B01001A_019, B01001A_020, B01001A_021, B01001A_001
B01001A_007, B01001A_008, B01001A_009, B01001A_010, B01001A_022, B01001A_023, B01001A_024, B01001A_025, B01001A_001
B01001A_011, B01001A_012, B01001A_013, B01001A_026, B01001A_027, B01001A_028, B01001A_001
B01001A_014, B01001A_015, B01001A_016, B01001A_029, B01001A_030, B01001A_031, B01001A_001
C15002A_003, C15002A_008, C15002A_001
C15002A_004, C15002A_009, C15002A_001
C15002A_005, C15002A_010, C15002A_001
C150

B19001B_002, B19001B_003, B19001B_004, B19001B_005, B19001B_001
B19001B_006, B19001B_007, B19001B_008, B19001B_009, B19001B_010, B19001B_001
B19001B_011, B19001B_012, B19001B_001
B19001B_013, B19001B_001
B19001B_013E B19001B_001E
B19001B_014, B19001B_001
B19001B_014E B19001B_001E
B19001B_015, B19001B_016, B19001B_017, B19001B_001
B19001C_002, B19001C_003, B19001C_004, B19001C_005, B19001C_001
B19001C_006, B19001C_007, B19001C_008, B19001C_009, B19001C_010, B19001C_001
B19001C_011, B19001C_012, B19001C_001
B19001C_013, B19001C_001
B19001C_013E B19001C_001E
B19001C_014, B19001C_001
B19001C_014E B19001C_001E
B19001C_015, B19001C_016, B19001C_017, B19001C_001
B19001D_002, B19001D_003, B19001D_004, B19001D_005, B19001D_001
B19001D_006, B19001D_007, B19001D_008, B19001D_009, B19001D_010, B19001D_001
B19001D_011, B19001D_012, B19001D_001
B19001D_013, B19001D_001
B19001D_013E B19001D_001E
B19001D_014, B19001D_001
B19001D_014E B19001D_001E
B19001D_015, B19001D_016, B19001D_017, B19001D_001
B190

Attribute  North Beach  Russian Hill  \
0            A_Total Population  5722.000000  12302.000000   
1    A_Group Quarter Population     0.000000      0.000000   
2           A_Female Population  2535.000000   6095.000000   
3  A_Population with Disability     0.000000     11.000000   
4                A_Foreign Born     0.177735      0.144123   

   Financial District    Chinatown      Nob Hill    Tenderloin        Marina  \
0        10768.000000  1572.000000  14148.000000  11453.000000  20319.000000   
1            0.000000     0.000000      0.000000      0.000000      0.000000   
2         3848.000000   778.000000   6480.000000   4751.000000  10815.000000   
3            0.000000     0.000000     23.000000      0.000000     28.000000   
4            0.242571     0.102417      0.157902      0.238104      0.102958   

   Pacific Heights  Presidio Heights  ...    Lakeshore  Inner Richmond  \
0     16851.000000       7336.000000  ...  5598.000000     11373.00000   
1         0.000000          0.000000  ...     0.000000         0.00000   
2      8444.000000       3605.000000  ...  2994.000000      5932.00000   
3        14.000000         41.000000  ...     0.000000        49.00000   
4         0.133701          0.094329  ...     0.318328         0.10947   

   Outer Richmond     Seacliff     Presidio  Mission Bay  Lincoln Park  \
0    20840.000000  1652.000000  2534.000000  6167.000000     87.000000   
1        0.000000     0.000000     0.000000     0.000000      0.000000   
2    10415.000000   865.000000  1407.000000  2986.000000      0.000000   
3       71.000000     0.000000     0.000000   124.000000      0.000000   
4        0.208925     0.088378     0.069455     0.235609      0.114943   

   Golden Gate Park  McLaren Park           sf  
0              22.0           0.0  392476.0000  
1               0.0           0.0       0.0000  
2               8.0           0.0  180287.0000  
3               0.0           0.0    1169.0000  
4               0.0           0.0       0.1728  

[5 rows x 43 columns]

#### Combine the calc results & Arrange data by geographies

In [56]:
df_all_calcs_fin = pd.concat([df_all_calcs, df_lan_calcs, df_race_calcs]).reset_index(drop = True)
print(len(df_all_calcs_fin))
df_all_calcs_fin.head()

359


Attribute   North Beach  Russian Hill  \
0                Total Population  11934.000000  18237.000000   
1        Group Quarter Population     17.000000      5.000000   
2               Female Population   5761.000000   9679.000000   
3  % Population with a Disability      0.145215      0.077315   
4                       Housholds   6308.000000   9601.000000   

   Financial District     Chinatown      Nob Hill    Tenderloin        Marina  \
0        22963.000000  14310.000000  26247.000000  29726.000000  25186.000000   
1          581.000000     55.000000    891.000000   1544.000000     98.000000   
2        10358.000000   7414.000000  12549.000000  13185.000000  13186.000000   
3            0.057092      0.162124      0.089381      0.246546      0.054941   
4        11967.000000   6751.000000  15225.000000  18082.000000  12832.000000   

   Pacific Heights  Presidio Heights  ...     Lakeshore  Inner Richmond  \
0     23953.000000      10445.000000  ...  14368.000000    22753.000000   
1       511.000000        158.000000  ...   2673.000000      161.000000   
2     12078.000000       5384.000000  ...   7591.000000    12463.000000   
3         0.082918          0.075954  ...      0.106695        0.093933   
4     12860.000000       5054.000000  ...   4913.000000     8897.000000   

   Outer Richmond     Seacliff     Presidio   Mission Bay  Lincoln Park  \
0    45745.000000  2416.000000  4073.000000  13330.000000         185.0   
1      191.000000     0.000000     0.000000    321.000000         185.0   
2    24160.000000  1247.000000  2208.000000   6755.000000           0.0   
3        0.110132     0.075745     0.026025      0.078245           0.0   
4    18980.000000   868.000000  1318.000000   6065.000000           0.0   

   Golden Gate Park  McLaren Park             sf  
0              32.0    153.000000  874784.000000  
1               0.0      0.000000   20169.000000  
2               8.0    123.000000  428538.000000  
3               0.0      0.529412       0.101049  
4              25.0    122.000000  362141.000000  

[5 rows x 43 columns]

In [57]:
# transpose dataset so that each row represents one geographic area
df_all_calcs_fin_tp = df_all_calcs_fin.T.reset_index()
df_all_calcs_fin_tp.columns = df_all_calcs_fin_tp.iloc[0]
df_all_calcs_fin_tp = df_all_calcs_fin_tp[1:].rename(columns={'Attribute': geo_summary_variable})
df_all_calcs_fin_tp = df_all_calcs_fin_tp.sort_values(by=[geo_summary_variable]).reset_index(drop = True)
df_all_calcs_fin_tp.head()

0           Neighborhood Total Population Group Quarter Population  \
0  Bayview Hunters Point          38480.0                    218.0   
1         Bernal Heights          26149.0                    178.0   
2    Castro/Upper Market          23138.0                     72.0   
3              Chinatown          14310.0                     55.0   
4              Excelsior          40980.0                    547.0   

0 Female Population % Population with a Disability Housholds  \
0           19453.0                       0.110507   11824.0   
1           12330.0                       0.080012    9190.0   
2            8550.0                       0.097161   11491.0   
3            7414.0                       0.162124    6751.0   
4           20632.0                       0.098616   11306.0   

0 Family Households Non-Family Households Single Person Households  \
0          0.693843              0.306157                  0.22319   
1          0.601741              0.398259                 0.224701   
2          0.331912              0.668088                 0.403359   
3          0.522885              0.477115                 0.420086   
4           0.74005               0.25995                 0.167699   

0 Households with Children  ... I_Household Income (50K-75K)  \
0                 0.351573  ...                     0.132716   
1                 0.302612  ...                     0.134158   
2                 0.122618  ...                     0.107399   
3                 0.145756  ...                     0.391566   
4                 0.311339  ...                     0.165758   

0 I_Household Income (75K-100K) I_Household Income (100K-125K)  \
0                       0.10751                       0.104938   
1                      0.041389                       0.095623   
2                      0.050119                       0.093079   
3                      0.210843                            0.0   
4                      0.126323                       0.170567   

0 I_Household Income (more than 125K) A_Household Income (less than 25K)  \
0                            0.289609                           0.112593   
1                            0.388202                           0.085378   
2                            0.437947                           0.084592   
3                                 0.0                            0.20943   
4                            0.253286                           0.096415   

0 A_Household Income (25K-50K) A_Household Income (50K-75K)  \
0                      0.08111                     0.104055   
1                     0.047395                     0.091597   
2                     0.061321                     0.061762   
3                     0.112939                     0.162281   
4                     0.126391                     0.162855   

0 A_Household Income (75K-100K) A_Household Income (100K-125K)  \
0                      0.068837                       0.067769   
1                      0.090084                        0.06605   
2                      0.080291                       0.069152   
3                      0.058114                       0.087719   
4                      0.101051                       0.065513   

0 A_Household Income (more than 125K)  
0                            0.565635  
1                            0.619496  
2                            0.642881  
3                            0.369518  
4                            0.447775  

[5 rows x 360 columns]

#### Midpoint export (Keep proceeding until the final export) 

In [58]:
# export dataset to csv
df_all_calcs_fin_tp.to_csv(os.path.join(download_path,geo_summary_variable+"_"+'profiles_by_geo_{}.csv'.format(year)), index = False)

## Repeat: 10 years ago

The code below basically repeats the same data compiling process as above, yet the data is from `year_past` set at the beginning of this notebook. The code needs new lookup tables that include attribute IDs corresponding to the past ACS data: 

- [attribute_lookup_past.csv]() 
- [race_attribute_loookup_past.csv]()
- [median_ranges_past.csv]()
- [race_median_ranges_past.csv]()

### Census Attribute IDs

In [62]:
# Create list of attribute IDs from attribute_lookup_past.csv
attribute_lookup_past_df = pd.read_csv (r'./lookup_tables/attribute_lookup_past.csv', dtype=str)
attribute_ids_past_extracted = attribute_lookup_past_df['attribute_id'].tolist()
attribute_ids_past = []
for attribute_id in attribute_ids_past_extracted:
    attribute_ids_past.extend(attribute_id.split(", "))
attribute_ids_past = list(set([x+"E" for x in attribute_ids_past]))
print(len(attribute_ids_past))
attribute_ids_past[:10]

323


['B19101_012E',
 'B16007_011E',
 'B19001_004E',
 'B01001_041E',
 'B25070_004E',
 'B25014_005E',
 'B25046_001E',
 'B25063_016E',
 'B25034_002E',
 'B23001_015E']

In [63]:
# Create list of attribute IDs from race_attribute_lookup_past.csv
race_attribute_lookup_past_df = pd.read_csv(r'./lookup_tables/race_attribute_lookup_past.csv', dtype=str)
race_attribute_ids_past_extracted = race_attribute_lookup_past_df['attribute_id'].tolist()
race_attribute_ids_past = []
for race_attribute_id in race_attribute_ids_past_extracted:
    race_attribute_ids_past.extend(race_attribute_id.split(", "))
race_attribute_ids_past = list(set([x+"E" for x in race_attribute_ids_past]))
print(len(race_attribute_ids_past))
race_attribute_ids_past[:10]

600


['B01001C_001E',
 'B07004D_001E',
 'C23002B_004E',
 'B01001D_022E',
 'C15002A_010E',
 'C15002H_005E',
 'B19001D_006E',
 'B01001B_003E',
 'B01001H_005E',
 'B19001D_009E']

In [64]:
# import median tables from median_ranges_past csv and add empty columns for rows 'households and 'cumulative_totals'
range_past_df = pd.read_csv (r'./lookup_tables/median_ranges_past.csv')
range_past_df['households']=0
range_past_df['cumulative_total']=0
range_past_df.head()

name           id  range_start  range_end  households  \
0  median_household_income  B19001_002E       2500.0     9999.0           0   
1  median_household_income  B19001_003E      10000.0    14999.0           0   
2  median_household_income  B19001_004E      15000.0    19999.0           0   
3  median_household_income  B19001_005E      20000.0    24999.0           0   
4  median_household_income  B19001_006E      25000.0    29999.0           0   

   cumulative_total  
0                 0  
1                 0  
2                 0  
3                 0  
4                 0

In [65]:
# import median tables from median_ranges_past_race csv and add empty columns for rows 'households and 'cumulative_totals'
range_past_race_df = pd.read_csv (r'./lookup_tables/median_ranges_past_race.csv')
range_past_race_df['households']=0
range_past_race_df['cumulative_total']=0
range_past_race_df.head()

name            id  range_start  range_end  \
0  A_median_household_income  B19001A_002E         2500       9999   
1  A_median_household_income  B19001A_003E        10000      14999   
2  A_median_household_income  B19001A_004E        15000      19999   
3  A_median_household_income  B19001A_005E        20000      24999   
4  A_median_household_income  B19001A_006E        25000      29999   

   households  cumulative_total  
0           0                 0  
1           0                 0  
2           0                 0  
3           0                 0  
4           0                 0

#### Compile data: Total Population - Past

In [68]:
# set geo variables for api call
tract_code = "*"
state_code = "06"
county_code = "075"

# split attributes into groups of 45, run a census query for each, merge outputs into a single df
split_attribute_ids_past = [attribute_ids_past[i:i+45] for i in range(0, len(attribute_ids_past), 45)]
split_attribute_ids_past[:] = (value for value in split_attribute_ids_past if value != ' ')

df_past = None
first = True
for ids in split_attribute_ids_past:
    census_url = build_census_url(tract_code, state_code, county_code, ids, year_past)
    returned_df = make_census_api_call(census_url)
    if first:
        df_past = returned_df
        first = False
    else:
        returned_df = returned_df.drop(columns=['state', 'county'])
        df_past = pd.merge(df_past, returned_df, on='tract', how='left')

df_past.head()

B19101_012E  B16007_011E  B19001_004E  B01001_041E  B25070_004E  \
0           27          217          209          105          268   
1           53          258          110          160          284   
2           14          182           36           48          209   
3           99          105          117          194          481   
4           51          280           20          129          158   

   B25014_005E  B25046_001E  B25063_016E  B25034_002E  B23001_015E  ...  \
0            0       1457.0            0           46            0  ...   
1            0       2790.0           45           10            0  ...   
2            0       1888.0            0            0           28  ...   
3            4       2191.0           13            0            0  ...   
4            0       1067.0            0           13            0  ...   

   B01001_030E  B16007_019E  B16003_006E  B06007_004E  B25014_007E  \
0           61            0            0          127            0   
1            0           13            0          233            0   
2           50            0           87          127            0   
3           67            0            0           68            0   
4            0            0            0          100            0   

   B25063_010E  B25075_003E  B23001_076E  B23001_097E  B23001_165E  
0           38            0            0            0           22  
1            0            0            0            0           12  
2            0            0            0            0           26  
3           11            0            0           13           23  
4            0            0            0           18           31  

[5 rows x 326 columns]

#### Compile data: Race/Ethnicity Groups - Past

In [69]:
# race/ethnicity: run a census query for each, merge outputs into a single df
split_race_attribute_past_ids = [race_attribute_ids_past[i:i+45] for i in range(0, len(race_attribute_ids_past), 45)]

first = False
for ids in split_race_attribute_past_ids:
    census_url = build_census_url(tract_code, state_code, county_code, ids, year_past)
    #print(census_url)
    returned_df = make_census_api_call(census_url)
    if first:
        df_past = returned_df
        first = False
    else:
        returned_df = returned_df.drop(columns=['state', 'county'])
        df_past = pd.merge(df_past, returned_df, on='tract', how='left')

df_past.head()

B19101_012E  B16007_011E  B19001_004E  B01001_041E  B25070_004E  \
0           27          217          209          105          268   
1           53          258          110          160          284   
2           14          182           36           48          209   
3           99          105          117          194          481   
4           51          280           20          129          158   

   B25014_005E  B25046_001E  B25063_016E  B25034_002E  B23001_015E  ...  \
0            0       1457.0            0           46            0  ...   
1            0       2790.0           45           10            0  ...   
2            0       1888.0            0            0           28  ...   
3            4       2191.0           13            0            0  ...   
4            0       1067.0            0           13            0  ...   

   B11001A_002E  B19101A_005E  B19001H_014E  B19101C_016E  B19001C_011E  \
0           283            12           119             0             0   
1           673             8           228             0             0   
2           415             0           150             0             0   
3           478             0           206             0             0   
4           523             0           244             0             0   

   C15002H_009E  B19101H_015E  B01001C_022E  B19001C_017E  B19101I_008E  
0            14            12             0             0             0  
1           104            21             0             0             0  
2           189            27             0             0             0  
3            13            19             0             0             0  
4           112            77             0             0             0  

[5 rows x 926 columns]

In [111]:
# import geo_lookup csv
geo_lookup_df = pd.read_csv (r'./lookup_tables/geo_lookup_2010.csv', dtype=str)
geo_lookup_df['tractid'] = geo_lookup_df['GEOID'].str[4:]

tract_tr_lookup = defaultdict(list)
tract_nb_lookup = defaultdict(list)
all_tracts = list(set(df_past['tract'].tolist()))

# create tract lookup dictionary for tracts 
for i in all_tracts:
    tract_tr_lookup[i].append(i) 
# create tract lookup dictionary for neighborhoods
for i, j in zip(geo_lookup_df['neighborhood'], geo_lookup_df['tractid']):
    tract_nb_lookup[i].append(j)
tract_nb_lookup["sf"]= all_tracts

    
first_4 = list(tract_nb_lookup.items())


# sets geo variables based on above choice
if geo_summary_variable == 'Tract':
    tract_lookup = tract_tr_lookup
    geo_path = r'./shps/tracts_2010/geo_export_f50126ea-5b6e-4471-a97d-e00c306d6496.shp'
    geo_merge_variable = 'tractce'
elif geo_summary_variable == 'Neighborhood':
    tract_lookup = tract_nb_lookup
    geo_path = r'./shps/neighborhoods/neighborhoods5/neighborhoods5.shp'
    geo_merge_variable = 'nhood'


In [112]:
tract_lookup['Mission Bay']

['060700']

### Run Socio-economic Profiles calc - Past

#### Total Population - Past

In [114]:
# run functions to calculate all stats and convert calc dictionary to pandas dataframe
all_calc_past_data = calc_socio_economic_data(df_past, attribute_lookup_past_df, range_past_df, tract_lookup)
df_all_calcs_past = pd.DataFrame.from_dict(all_calc_past_data).reset_index()

df_all_calcs_past.rename(columns = {'index':'Attribute'}, inplace = True) 
df_all_calcs_past.head()


11
B01001_001
B26001_001
B01001_026
B11001_001
B11001_002, B11001_001
B11001_002E B11001_001E
B11001_007, B11001_001
B11001_007E B11001_001E
B11001_008, B11001_001
B11001_008E B11001_001E
B11005_002, B11001_001
B11005_002E B11001_001E
B11006_002, B11001_001
B11006_002E B11001_001E
B01001_001
B11002_001, B11001_001
B11002_001E B11001_001E
B11002_002, B11001_002
B11002_002E B11001_002E
B02001_005, B02001_001
B02001_005E B02001_001E
B02001_003, B02001_001
B02001_003E B02001_001E
B02001_002, B02001_001
B02001_002E B02001_001E
B02010_001, B02001_001
B02010_001E B02001_001E
B02001_006, B02001_001
B02001_006E B02001_001E
B02001_008, B02001_007, B02001_001
B03001_003, B03001_001
B03001_003E B03001_001E
B01001_003, B01001_027, B01001_001
B01001_004, B01001_005, B01001_006, B01001_028, B01001_029, B01001_030, B01001_001
B01001_007, B01001_008, B01001_009, B01001_010, B01001_031, B01001_032, B01001_033, B01001_034, B01001_011, B01001_012, B01001_035, B01001_036, B01001_001
B01001_013, B01001_014,

B25075_002, B25075_003, B25075_004, B25075_005, B25075_006, B25075_007, B25075_008, B25075_009, B25075_010, B25075_011, B25075_012, B25075_013, B25075_014, B25075_015, B25075_016, B25075_017, B25075_018, B25075_019, B25075_020, B25075_021, B25075_022, B25075_023, B25075_024, B25075_025
                  name           id  range_start  range_end  households  \
108  median_home_value  B25075_002E       9999.0     9999.0           0   
109  median_home_value  B25075_003E      10000.0    14999.0           0   
110  median_home_value  B25075_004E      15000.0    19999.0           0   
111  median_home_value  B25075_005E      20000.0    24999.0           0   
112  median_home_value  B25075_006E      25000.0    29999.0           0   
113  median_home_value  B25075_007E      30000.0    34999.0           0   
114  median_home_value  B25075_008E      35000.0    39999.0           0   
115  median_home_value  B25075_009E      40000.0    49999.0           0   
116  median_home_value  B25075_010E   

B19025_001, B01001_001
B19025_001E B01001_001E
B17001_002, B17001_001
B17001_002E B17001_001E
B19001_002, B19001_003, B19001_004, B19001_005, B19001_001
B19001_006, B19001_007, B19001_008, B19001_009, B19001_010, B19001_001
B19001_011, B19001_012, B19001_001
B19001_013, B19001_001
B19001_013E B19001_001E
B19001_014, B19001_001
B19001_014E B19001_001E
B19001_015, B19001_016, B19001_017, B19001_001
B23001_094, B23001_101, B23001_108, B23001_115, B23001_122, B23001_129, B23001_136, B23001_143, B23001_150, B23001_157, B23001_162, B23001_167, B23001_172, B23001_008, B23001_015, B23001_022, B23001_029, B23001_036, B23001_043, B23001_050, B23001_057, B23001_064, B23001_071, B23001_076, B23001_081, B23001_086
B23001_090, B23001_097, B23001_104, B23001_111, B23001_118, B23001_125, B23001_132, B23001_139, B23001_146, B23001_153, B23001_160, B23001_165, B23001_170, B23001_004, B23001_011, B23001_018, B23001_025, B23001_032, B23001_039, B23001_046, B23001_053, B23001_060, B23001_067, B23001_074, B

B19101_001, B19101_002, B19101_003, B19101_004, B19101_005, B19101_006, B19101_007, B19101_008, B19101_009, B19101_010, B19101_011, B19101_012, B19101_013, B19101_014, B19101_015, B19101_016, B19101_017
                    name           id  range_start  range_end  households  \
16  median_family_income  B19101_002E       2500.0     9999.0           0   
17  median_family_income  B19101_003E      10000.0    14999.0           0   
18  median_family_income  B19101_004E      15000.0    19999.0           0   
19  median_family_income  B19101_005E      20000.0    24999.0           0   
20  median_family_income  B19101_006E      25000.0    29999.0           0   
21  median_family_income  B19101_007E      30000.0    34999.0           0   
22  median_family_income  B19101_008E      35000.0    39999.0           0   
23  median_family_income  B19101_009E      40000.0    44999.0           0   
24  median_family_income  B19101_010E      45000.0    49999.0           0   
25  median_family_income  B

B15002_003, B15002_004, B15002_005, B15002_006, B15002_007, B15002_008, B15002_009, B15002_010, B15002_020, B15002_021, B15002_022, B15002_023, B15002_024, B15002_025, B15002_026, B15002_027, B15002_001
B15002_011, B15002_028, B15002_001
B15002_012, B15002_013, B15002_014, B15002_029, B15002_030, B15002_031, B15002_001
B15002_015, B15002_016, B15002_017, B15002_018, B15002_032, B15002_033, B15002_034, B15002_035, B15002_001
B05002_013, B05002_001
B05002_013E B05002_001E
B05002_014, B05002_001
B05002_014E B05002_001E
B16007_003, B16007_009, B16007_015, B16007_001
B16007_004, B16007_010, B16007_016, B16007_001
B16007_006, B16007_012, B16007_018, B16007_001
B16007_005, B16007_011, B16007_017, B16007_001
B16007_007, B16007_013, B16007_019, B16007_001
B16003_002, B16003_008, B16004_001
B16003_004, B16003_009, B16004_001
B16003_006, B16003_011, B16004_001
B16003_005, B16003_010, B16004_001
B16003_007, B16003_012, B16004_001
B06007_002, B06007_004, B06007_007, B06007_001
B06007_034, B06007_03

B25046_001
B25046_002, B25046_001
B25046_002E B25046_001E
B25046_003, B25046_001
B25046_003E B25046_001E
B25046_001, B01001_001
B25046_001E B01001_001E
B25044_003, B25044_010, B25044_001
B25044_003, B25044_002
B25044_003E B25044_002E
B25044_010, B25044_009
B25044_010E B25044_009E
B19001_001, B19001_002, B19001_003, B19001_004, B19001_005, B19001_006, B19001_007, B19001_008, B19001_009, B19001_010, B19001_011, B19001_012, B19001_013, B19001_014, B19001_015, B19001_016, B19001_017
                       name           id  range_start  range_end  households  \
0   median_household_income  B19001_002E       2500.0     9999.0           0   
1   median_household_income  B19001_003E      10000.0    14999.0           0   
2   median_household_income  B19001_004E      15000.0    19999.0           0   
3   median_household_income  B19001_005E      20000.0    24999.0           0   
4   median_household_income  B19001_006E      25000.0    29999.0           0   
5   median_household_income  B19001_

Attribute  Bayview Hunters Point  Bernal Heights  \
0          Total Population            34464.00000     24999.00000   
1  Group Quarter Population                0.00000       124.00000   
2         Female Population            17373.00000     12343.00000   
3                 Housholds            10258.00000      9079.00000   
4         Family Households                0.72675         0.53398   

   Castro/Upper Market     Chinatown     Excelsior  \
0         19787.000000  15319.000000  39090.000000   
1             0.000000      0.000000   1222.000000   
2          6854.000000   7839.000000  19809.000000   
3         11079.000000   7230.000000  10159.000000   
4             0.227096      0.494467      0.756669   

   Financial District/South Beach   Glen Park  Golden Gate Park  \
0                    13822.000000  8238.00000         30.000000   
1                     1183.000000     0.00000          0.000000   
2                     5719.000000  4115.00000         12.000000   
3                     7928.000000  3814.00000         21.000000   
4                        0.302346     0.46775          0.428571   

   Haight Ashbury  ...     Seacliff  South of Market  Sunset/Parkside  \
0    17374.000000  ...  2383.000000      16152.00000     76922.000000   
1      189.000000  ...     0.000000       2238.00000       468.000000   
2     7875.000000  ...  1225.000000       7286.00000     38990.000000   
3     8288.000000  ...   905.000000       7874.00000     26170.000000   
4        0.302124  ...     0.762431          0.29807         0.677646   

     Tenderloin  Treasure Island   Twin Peaks  Visitacion Valley  \
0  24688.000000      2077.000000  7418.000000        17864.00000   
1    791.000000        44.000000  1213.000000          146.00000   
2   9434.000000       928.000000  3244.000000         8821.00000   
3  15483.000000       652.000000  3478.000000         4740.00000   
4      0.194923         0.478528     0.351064            0.78692   

   West of Twin Peaks  Western Addition             sf  
0        36105.000000      19271.000000  789172.000000  
1            0.000000        218.000000   14781.000000  
2        18030.000000       9715.000000  389489.000000  
3        13570.000000      10909.000000  335956.000000  
4            0.668902          0.305344       0.447466  

[5 rows x 43 columns]

#### Race/Ethnicity Groups - Past

In [115]:
# run functions to calculate all race/ethnicity stats, convert dictionary to dataframe, append the datafrmae to df_all_calcs
race_calc_past_data = calc_socio_economic_data(df_past, race_attribute_lookup_past_df, range_past_race_df, tract_lookup)
df_race_calcs_past = pd.DataFrame.from_dict(race_calc_past_data).reset_index()
df_race_calcs_past.rename(columns = {'index':'Attribute'}, inplace = True)
df_race_calcs_past.head()


11
B01001A_001
B01001A_017, B01001A_001
B01001A_017E B01001A_001E
B06004A_005, B06004A_001
B06004A_005E B06004A_001E
B05003A_006, B05003A_011, B05003A_017, B05003A_022, B05003A_001
B11001A_001
B11001A_002, B11001A_001
B11001A_002E B11001A_001E
B11001A_007, B11001A_001
B11001A_007E B11001A_001E
B11001A_008, B11001A_001
B11001A_008E B11001A_001E
B11002A_001, B11001A_001
B11002A_001E B11001A_001E
B11002A_002, B11001A_002
B11002A_002E B11001A_002E
B01001A_003, B01001A_018, B01001A_001
B01001A_004, B01001A_005, B01001A_006, B01001A_019, B01001A_020, B01001A_021, B01001A_001
B01001A_007, B01001A_008, B01001A_009, B01001A_010, B01001A_022, B01001A_023, B01001A_024, B01001A_025, B01001A_001
B01001A_011, B01001A_012, B01001A_013, B01001A_026, B01001A_027, B01001A_028, B01001A_001
B01001A_014, B01001A_015, B01001A_016, B01001A_029, B01001A_030, B01001A_031, B01001A_001
C15002A_003, C15002A_008, C15002A_001
C15002A_004, C15002A_009, C15002A_001
C15002A_005, C15002A_010, C15002A_001
C15002A_006, C

B11002I_002, B11001I_002
B11002I_002E B11001I_002E
B01001I_003, B01001I_018, B01001I_001
B01001I_004, B01001I_005, B01001I_006, B01001I_019, B01001I_020, B01001I_021, B01001I_001
B01001I_007, B01001I_008, B01001I_009, B01001I_010, B01001I_022, B01001I_023, B01001I_024, B01001I_025, B01001I_001
B01001I_011, B01001I_012, B01001I_013, B01001I_026, B01001I_027, B01001I_028, B01001I_001
B01001I_014, B01001I_015, B01001I_016, B01001I_029, B01001I_030, B01001I_031, B01001I_001
C15002I_003, C15002I_008, C15002I_001
C15002I_004, C15002I_009, C15002I_001
C15002I_005, C15002I_010, C15002I_001
C15002I_006, C15002I_011, C15002I_001
B19025I_001, B01001I_001
B19025I_001E B01001I_001E
B17001I_002, B17001I_001
B17001I_002E B17001I_001E
C23002I_008, C23002I_013, C23002I_021, C23002I_026
C23002I_004, C23002I_011, C23002I_017, C23002I_024
B25003I_002, B25003I_001
B25003I_002E B25003I_001E
B25003I_003, B25003I_001
B25003I_003E B25003I_001E
B07004I_002, B07004I_001
B07004I_002E B07004I_001E
B19001A_002, B19

5
B01001A_001
B01001A_017, B01001A_001
B01001A_017E B01001A_001E
B06004A_005, B06004A_001
B06004A_005E B06004A_001E
B05003A_006, B05003A_011, B05003A_017, B05003A_022, B05003A_001
B11001A_001
B11001A_002, B11001A_001
B11001A_002E B11001A_001E
B11001A_007, B11001A_001
B11001A_007E B11001A_001E
B11001A_008, B11001A_001
B11001A_008E B11001A_001E
B11002A_001, B11001A_001
B11002A_001E B11001A_001E
B11002A_002, B11001A_002
B11002A_002E B11001A_002E
B01001A_003, B01001A_018, B01001A_001
B01001A_004, B01001A_005, B01001A_006, B01001A_019, B01001A_020, B01001A_021, B01001A_001
B01001A_007, B01001A_008, B01001A_009, B01001A_010, B01001A_022, B01001A_023, B01001A_024, B01001A_025, B01001A_001
B01001A_011, B01001A_012, B01001A_013, B01001A_026, B01001A_027, B01001A_028, B01001A_001
B01001A_014, B01001A_015, B01001A_016, B01001A_029, B01001A_030, B01001A_031, B01001A_001
C15002A_003, C15002A_008, C15002A_001
C15002A_004, C15002A_009, C15002A_001
C15002A_005, C15002A_010, C15002A_001
C15002A_006, C1

B19101D_002, B19101D_003, B19101D_004, B19101D_005, B19101D_006, B19101D_007, B19101D_008, B19101D_009, B19101D_010, B19101D_011, B19101D_012, B19101D_013, B19101D_014, B19101D_015, B19101D_016, B19101D_017
                       name            id  range_start  range_end  households  \
112  D_median_family_income  B19101D_002E         2500       9999           0   
113  D_median_family_income  B19101D_003E        10000      14999           0   
114  D_median_family_income  B19101D_004E        15000      19999           0   
115  D_median_family_income  B19101D_005E        20000      24999           0   
116  D_median_family_income  B19101D_006E        25000      29999           0   
117  D_median_family_income  B19101D_007E        30000      34999           0   
118  D_median_family_income  B19101D_008E        35000      39999           0   
119  D_median_family_income  B19101D_009E        40000      44999           0   
120  D_median_family_income  B19101D_010E        45000      4999

B11001I_008E B11001I_001E
B11002I_001, B11001I_001
B11002I_001E B11001I_001E
B11002I_002, B11001I_002
B11002I_002E B11001I_002E
B01001I_003, B01001I_018, B01001I_001
B01001I_004, B01001I_005, B01001I_006, B01001I_019, B01001I_020, B01001I_021, B01001I_001
B01001I_007, B01001I_008, B01001I_009, B01001I_010, B01001I_022, B01001I_023, B01001I_024, B01001I_025, B01001I_001
B01001I_011, B01001I_012, B01001I_013, B01001I_026, B01001I_027, B01001I_028, B01001I_001
B01001I_014, B01001I_015, B01001I_016, B01001I_029, B01001I_030, B01001I_031, B01001I_001
C15002I_003, C15002I_008, C15002I_001
C15002I_004, C15002I_009, C15002I_001
C15002I_005, C15002I_010, C15002I_001
C15002I_006, C15002I_011, C15002I_001
B19025I_001, B01001I_001
B19025I_001E B01001I_001E
B17001I_002, B17001I_001
B17001I_002E B17001I_001E
C23002I_008, C23002I_013, C23002I_021, C23002I_026
C23002I_004, C23002I_011, C23002I_017, C23002I_024
B25003I_002, B25003I_001
B25003I_002E B25003I_001E
B25003I_003, B25003I_001
B25003I_003E B25

5
B01001A_001
B01001A_017, B01001A_001
B01001A_017E B01001A_001E
B06004A_005, B06004A_001
B06004A_005E B06004A_001E
B05003A_006, B05003A_011, B05003A_017, B05003A_022, B05003A_001
B11001A_001
B11001A_002, B11001A_001
B11001A_002E B11001A_001E
B11001A_007, B11001A_001
B11001A_007E B11001A_001E
B11001A_008, B11001A_001
B11001A_008E B11001A_001E
B11002A_001, B11001A_001
B11002A_001E B11001A_001E
B11002A_002, B11001A_002
B11002A_002E B11001A_002E
B01001A_003, B01001A_018, B01001A_001
B01001A_004, B01001A_005, B01001A_006, B01001A_019, B01001A_020, B01001A_021, B01001A_001
B01001A_007, B01001A_008, B01001A_009, B01001A_010, B01001A_022, B01001A_023, B01001A_024, B01001A_025, B01001A_001
B01001A_011, B01001A_012, B01001A_013, B01001A_026, B01001A_027, B01001A_028, B01001A_001
B01001A_014, B01001A_015, B01001A_016, B01001A_029, B01001A_030, B01001A_031, B01001A_001
C15002A_003, C15002A_008, C15002A_001
C15002A_004, C15002A_009, C15002A_001
C15002A_005, C15002A_010, C15002A_001
C15002A_006, C1

B11001I_008, B11001I_001
B11001I_008E B11001I_001E
B11002I_001, B11001I_001
B11002I_001E B11001I_001E
B11002I_002, B11001I_002
B11002I_002E B11001I_002E
B01001I_003, B01001I_018, B01001I_001
B01001I_004, B01001I_005, B01001I_006, B01001I_019, B01001I_020, B01001I_021, B01001I_001
B01001I_007, B01001I_008, B01001I_009, B01001I_010, B01001I_022, B01001I_023, B01001I_024, B01001I_025, B01001I_001
B01001I_011, B01001I_012, B01001I_013, B01001I_026, B01001I_027, B01001I_028, B01001I_001
B01001I_014, B01001I_015, B01001I_016, B01001I_029, B01001I_030, B01001I_031, B01001I_001
C15002I_003, C15002I_008, C15002I_001
C15002I_004, C15002I_009, C15002I_001
C15002I_005, C15002I_010, C15002I_001
C15002I_006, C15002I_011, C15002I_001
B19025I_001, B01001I_001
B19025I_001E B01001I_001E
B17001I_002, B17001I_001
B17001I_002E B17001I_001E
C23002I_008, C23002I_013, C23002I_021, C23002I_026
C23002I_004, C23002I_011, C23002I_017, C23002I_024
B25003I_002, B25003I_001
B25003I_002E B25003I_001E
B25003I_003, B25

B11001I_008E B11001I_001E
B11002I_001, B11001I_001
B11002I_001E B11001I_001E
B11002I_002, B11001I_002
B11002I_002E B11001I_002E
B01001I_003, B01001I_018, B01001I_001
B01001I_004, B01001I_005, B01001I_006, B01001I_019, B01001I_020, B01001I_021, B01001I_001
B01001I_007, B01001I_008, B01001I_009, B01001I_010, B01001I_022, B01001I_023, B01001I_024, B01001I_025, B01001I_001
B01001I_011, B01001I_012, B01001I_013, B01001I_026, B01001I_027, B01001I_028, B01001I_001
B01001I_014, B01001I_015, B01001I_016, B01001I_029, B01001I_030, B01001I_031, B01001I_001
C15002I_003, C15002I_008, C15002I_001
C15002I_004, C15002I_009, C15002I_001
C15002I_005, C15002I_010, C15002I_001
C15002I_006, C15002I_011, C15002I_001
B19025I_001, B01001I_001
B19025I_001E B01001I_001E
B17001I_002, B17001I_001
B17001I_002E B17001I_001E
C23002I_008, C23002I_013, C23002I_021, C23002I_026
C23002I_004, C23002I_011, C23002I_017, C23002I_024
B25003I_002, B25003I_001
B25003I_002E B25003I_001E
B25003I_003, B25003I_001
B25003I_003E B25

5
B01001A_001
B01001A_017, B01001A_001
B01001A_017E B01001A_001E
B06004A_005, B06004A_001
B06004A_005E B06004A_001E
B05003A_006, B05003A_011, B05003A_017, B05003A_022, B05003A_001
B11001A_001
B11001A_002, B11001A_001
B11001A_002E B11001A_001E
B11001A_007, B11001A_001
B11001A_007E B11001A_001E
B11001A_008, B11001A_001
B11001A_008E B11001A_001E
B11002A_001, B11001A_001
B11002A_001E B11001A_001E
B11002A_002, B11001A_002
B11002A_002E B11001A_002E
B01001A_003, B01001A_018, B01001A_001
B01001A_004, B01001A_005, B01001A_006, B01001A_019, B01001A_020, B01001A_021, B01001A_001
B01001A_007, B01001A_008, B01001A_009, B01001A_010, B01001A_022, B01001A_023, B01001A_024, B01001A_025, B01001A_001
B01001A_011, B01001A_012, B01001A_013, B01001A_026, B01001A_027, B01001A_028, B01001A_001
B01001A_014, B01001A_015, B01001A_016, B01001A_029, B01001A_030, B01001A_031, B01001A_001
C15002A_003, C15002A_008, C15002A_001
C15002A_004, C15002A_009, C15002A_001
C15002A_005, C15002A_010, C15002A_001
C15002A_006, C1

Attribute  Bayview Hunters Point  Bernal Heights  \
0  A_Total Population            8594.000000    16652.000000   
1    A_Percent Female               0.498604        0.484747   
2      A_Foreign Born               0.406214        0.237929   
3       A_Naturalized               0.136840        0.082212   
4        A_Households            2186.000000     6683.000000   

   Castro/Upper Market    Chinatown     Excelsior  \
0         16325.000000  1535.000000  13948.000000   
1             0.337029     0.363518      0.495913   
2             0.115161     0.145277      0.400989   
3             0.058560     0.072964      0.197161   
4          9588.000000  1124.000000   4324.000000   

   Financial District/South Beach    Glen Park  Golden Gate Park  \
0                     8333.000000  6086.000000               0.0   
1                        0.385935     0.482090               0.0   
2                        0.203408     0.138350               0.0   
3                        0.110764     0.068189               0.0   
4                     5042.000000  2962.000000               0.0   

   Haight Ashbury  ...     Seacliff  South of Market  Sunset/Parkside  \
0    13349.000000  ...  1736.000000      6543.000000     28351.000000   
1        0.443029  ...     0.498848         0.363289         0.486508   
2        0.114615  ...     0.054147         0.163534         0.235195   
3        0.027343  ...     0.048963         0.070151         0.175479   
4     6515.000000  ...   733.000000      3651.000000     12574.000000   

    Tenderloin  Treasure Island   Twin Peaks  Visitacion Valley  \
0  9830.000000      1165.000000  4547.000000        2807.000000   
1     0.360631         0.408584     0.391907           0.482722   
2     0.201729         0.248927     0.162305           0.410403   
3     0.087996         0.144206     0.068397           0.142501   
4  7228.000000       388.000000  2461.000000         925.000000   

   West of Twin Peaks  Western Addition             sf  
0        20809.000000       9656.000000  406874.000000  
1            0.483108          0.452775       0.470755  
2            0.146523          0.283451       0.204395  
3            0.104186          0.160004       0.100869  
4         8987.000000       5911.000000  200463.000000  

[5 rows x 43 columns]

#### Combine the calc results & Arrange data by geographies

In [116]:
df_all_calcs_past_fin = pd.concat([df_all_calcs_past, df_race_calcs_past]).reset_index(drop = True)
df_all_calcs_past_fin.head()

Attribute  Bayview Hunters Point  Bernal Heights  \
0          Total Population            34464.00000     24999.00000   
1  Group Quarter Population                0.00000       124.00000   
2         Female Population            17373.00000     12343.00000   
3                 Housholds            10258.00000      9079.00000   
4         Family Households                0.72675         0.53398   

   Castro/Upper Market     Chinatown     Excelsior  \
0         19787.000000  15319.000000  39090.000000   
1             0.000000      0.000000   1222.000000   
2          6854.000000   7839.000000  19809.000000   
3         11079.000000   7230.000000  10159.000000   
4             0.227096      0.494467      0.756669   

   Financial District/South Beach   Glen Park  Golden Gate Park  \
0                    13822.000000  8238.00000         30.000000   
1                     1183.000000     0.00000          0.000000   
2                     5719.000000  4115.00000         12.000000   
3                     7928.000000  3814.00000         21.000000   
4                        0.302346     0.46775          0.428571   

   Haight Ashbury  ...     Seacliff  South of Market  Sunset/Parkside  \
0    17374.000000  ...  2383.000000      16152.00000     76922.000000   
1      189.000000  ...     0.000000       2238.00000       468.000000   
2     7875.000000  ...  1225.000000       7286.00000     38990.000000   
3     8288.000000  ...   905.000000       7874.00000     26170.000000   
4        0.302124  ...     0.762431          0.29807         0.677646   

     Tenderloin  Treasure Island   Twin Peaks  Visitacion Valley  \
0  24688.000000      2077.000000  7418.000000        17864.00000   
1    791.000000        44.000000  1213.000000          146.00000   
2   9434.000000       928.000000  3244.000000         8821.00000   
3  15483.000000       652.000000  3478.000000         4740.00000   
4      0.194923         0.478528     0.351064            0.78692   

   West of Twin Peaks  Western Addition             sf  
0        36105.000000      19271.000000  789172.000000  
1            0.000000        218.000000   14781.000000  
2        18030.000000       9715.000000  389489.000000  
3        13570.000000      10909.000000  335956.000000  
4            0.668902          0.305344       0.447466  

[5 rows x 43 columns]

In [117]:
# transpose dataset for second geo view of dataset
df_all_calcs_past_fin_tp = df_all_calcs_past_fin.T.reset_index()
df_all_calcs_past_fin_tp.columns = df_all_calcs_past_fin_tp.iloc[0]
df_all_calcs_past_fin_tp = df_all_calcs_past_fin_tp[1:].rename(columns={'Attribute': geo_summary_variable})
df_all_calcs_past_fin_tp = df_all_calcs_past_fin_tp.sort_values(by=[geo_summary_variable])
df_all_calcs_past_fin_tp.head()

0           Neighborhood Total Population Group Quarter Population  \
1  Bayview Hunters Point          34464.0                      0.0   
2         Bernal Heights          24999.0                    124.0   
3    Castro/Upper Market          19787.0                      0.0   
4              Chinatown          15319.0                      0.0   
5              Excelsior          39090.0                   1222.0   

0 Female Population Housholds Family Households Non-Family Households  \
1           17373.0   10258.0           0.72675               0.27325   
2           12343.0    9079.0           0.53398               0.46602   
3            6854.0   11079.0          0.227096              0.772904   
4            7839.0    7230.0          0.494467              0.505533   
5           19809.0   10159.0          0.756669              0.243331   

0 Single Person Households Households with Children  \
1                 0.231819                 0.435368   
2                 0.265117                 0.286265   
3                 0.473599                 0.087824   
4                 0.468741                 0.147026   
5                 0.173344                 0.375431   

0 Households with 60 years and older  ... B_Median Household Income  \
1                           0.362644  ...               32267.02509   
2                           0.270184  ...              33181.818182   
3                           0.208142  ...              53404.255319   
4                           0.543154  ...                   55000.0   
5                           0.421695  ...              51021.505376   

0 B_Median Family Income C_Median Household Income C_Median Family Income  \
1           41841.085271              44523.809524           41428.571429   
2           37857.142857             113541.666667               123437.5   
3                55000.0             130357.142857               137500.0   
4               168750.0              41136.363636                    0.0   
5                39000.0                   80500.0                71250.0   

0 D_Median Household Income D_Median Family Income H_Median Household Income  \
1                  68781.25           67728.426396              81052.631579   
2              66073.943662           66660.447761             102339.901478   
3             117721.518987           98214.285714             102875.302663   
4              15971.168437           22384.417808              58833.333333   
5              79234.417344           80765.086207              69948.347107   

0 H_Median Family Income I_Median Household Income I_Median Family Income  
1           80357.142857              47955.974843           39908.256881  
2          124426.229508              61212.871287                62625.0  
3          156902.356902              67932.692308              83203.125  
4               138437.5               18589.74359          208333.666667  
5           83928.571429              67783.964365           63567.567568  

[5 rows x 262 columns]

### Export the socio-economic profiles - past

In [118]:
# export the view to csv
df_all_calcs_past_fin_tp.to_csv(os.path.join(download_path,geo_summary_variable+"_"+'profiles_by_geo_{}.csv'.format(year_past)), index = False)

## Combine the present and past profiles 

In [119]:
# get both dataset views for the current year and 10 years ago 
data_year_df = pd.read_csv (r'./output/'+geo_summary_variable+"_"+'profiles_by_geo_{}.csv'.format(year), dtype=str)
data_year2_df = pd.read_csv (r'./output/'+geo_summary_variable+"_"+'profiles_by_geo_{}.csv'.format(year_past), dtype=str)

data_joined_years_df= data_year_df.merge(data_year2_df, on=geo_summary_variable, suffixes=("", "_10"), how='left')


In [ ]:
len(data_joined_years_df.columns)

### Export the final socio-economic profiles data 

In [120]:
# export the final data view 
data_joined_years_df.to_csv(os.path.join(download_path,geo_summary_variable+"_"+'profiles_by_geo_{}_{}.csv'.format(year, year_past)), index = False)


## Repeat for Tract-level Summary

In [ ]:
geo_summary_variable

If the geo_summary_variable is 'Neighborhood',

Go back to the top, rerun the code cell by cell, once you reach 'Calculate Socioeconomic Profiles' section, change the summary variable to 'Tract' and keep running the following code until you reach this point again. 

# Part 2. Non-Census data

In SFNP, there are four groups of data that are derived from sources other than ACS: 
- Affordable Housing
- Eviction 
- Equity Geographies/Project Boundaries 
- Built Environments 

Unlike the ACS data, these data are either 1) manually compiled by staff in SF Planning and located under the resources folder in this repository; or 2) derived from [DataSF](https://datasf.org/opendata/). 

The code below does:
- load the csv files
- aggregate the data by geographic areas
- add the result as new attributes to the socio-economic profile data created and saved by the code in the ACS 5 years section above.  



In [ ]:
# load the socioeconomic profiles data 
neigh_data = pd.read_csv(os.path.join(download_path,'Neighborhood_profiles_by_geo_{}_{}.csv'.format(year, year_past)))
tract_data = pd.read_csv(os.path.join(download_path,'Tract_profiles_by_geo_{}_{}.csv'.format(year, year_past))).convert_dtypes()
tract_data['Tract']=tract_data['Tract'].astype(int)

In [ ]:
# load the neighborhood/census tract shapefiles as geopandas dataframe for spatial join 
tract_path = r'./shps/tracts_2020/tracts_sf.shp'
neigh_path = r'./shps/neighborhoods/neighborhoods5/neighborhoods5.shp'

tract_df = gpd.read_file(tract_path).convert_dtypes()
neigh_df = gpd.read_file(neigh_path)

tract_df['tractce'] = tract_df['tractce'].astype(int)

neighborhood_list = neigh_df['nhood'].tolist()
tract_list = tract_df['tractce'].tolist()

geo_lookup_df = pd.read_csv(r'./lookup_tables/geo_lookup_{}.csv'.format(year))

## Affordable Housing (Affordable units + SROs + Rent-controlled)

This data was compiled by James Papas and Michael Webster in the SF Planning Department. While the dataset provides data for 2020, there is no maintenance plan for this data yet. Three csv files were derived from the original dataset: 
    - [affordable_housing_2021_for_NP.csv]()
    - [SRO_Points_for_NP.csv]()
    - [rent_controlled_2019_for_NP.csv]()

### Affordable Housing

In [ ]:
# load the affordable housing data 
aff_df = pd.read_csv (r'./resources/affordable_housing_2021_for_NP.csv')
aff_df['tot_units'] = aff_df.tot_units + (aff_df.tot_units == 0) * (aff_df.aff_unit)
 
aff_df['aff_unit_ratio'] = aff_df['aff_unit']/aff_df['tot_units']
aff_df[['aff_unit', 'tot_units', 'aff_unit_ratio']] = aff_df[['aff_unit', 'tot_units', 'aff_unit_ratio']].astype(float)
print(aff_df['neighborhood'])
aff_df.head()

In [ ]:
# aggregate the number of affordable units into geographic areas (neighborhood, census tract)
aff_df_by_neighborhood = aff_df.groupby("neighborhood").agg({'aff_unit':['count','sum'],'tot_units':'sum','aff_unit_ratio':'mean'})
aff_df_by_neighborhood.columns = ['aff_count', 'aff_unit_sum', 'aff_tot_units_sum', 'aff_mean_aff_ratio']
aff_df_by_neighborhood = aff_df_by_neighborhood.reset_index()

aff_df_by_tract = aff_df.groupby("tractce").agg({'aff_unit':['count','sum'],'tot_units':'sum','aff_unit_ratio':'mean'})
aff_df_by_tract.columns = ['aff_count', 'aff_unit_sum', 'aff_tot_units_sum', 'aff_mean_aff_ratio']
aff_df_by_tract = aff_df_by_tract.reset_index()

aff_df_by_tract.head()

In [ ]:
aff_df_by_tract.dtypes

In [ ]:
# combine the data to the socioeconomic profiles data 
neigh_data = neigh_data.merge(aff_df_by_neighborhood, how= 'left', left_on = 'Neighborhood', right_on = 'neighborhood')
neigh_data= neigh_data.drop(['neighborhood'], axis=1)
neigh_data.head()

In [ ]:
# combine the data to the socioeconomic profiles data 
tract_data = tract_data.merge(aff_df_by_tract, how='left', left_on = 'Tract', right_on = 'tractce')
tract_data = tract_data.drop(['tractce'], axis=1)
tract_data.head()

### SROs

In [ ]:
# load the SRO data 
sro_df = pd.read_csv (r'./resources/SRO_Points_for_NP.csv')
print(sro_df.columns)
sro_df['residential_unit_ratio'] = sro_df['CERT_RESID']/(sro_df['CERT_RESID']+sro_df['CERT_TOURI'])

In [ ]:
# aggregate the raw data into geographic units (neighborhood, census tract)
sro_df_by_neighborhood = sro_df.groupby("NHOOD").agg({'CERT_RESID':['count','sum'],'CERT_TOURI':'sum','residential_unit_ratio':'mean'})
sro_df_by_neighborhood.columns = ['sro_count', 'sro_residential_unit', 'sro_tourist_unit', 'sro_mean_residential_ratio']
sro_df_by_neighborhood = sro_df_by_neighborhood.reset_index()

sro_df_by_tract = sro_df.groupby("tractce").agg({'CERT_RESID':['count','sum'],'CERT_TOURI':'sum','residential_unit_ratio':'mean'})
sro_df_by_tract.columns = ['sro_count', 'sro_residential_unit', 'sro_tourist_unit', 'sro_mean_residential_ratio']
sro_df_by_tract = sro_df_by_tract.reset_index()

In [ ]:
# combine the data to the socioeconomic profiles data 
neigh_data = neigh_data.merge(sro_df_by_neighborhood, how= 'left', left_on = 'Neighborhood', right_on = 'NHOOD')
neigh_data= neigh_data.drop(['NHOOD'], axis=1)
neigh_data.head()

In [ ]:
# combine the data to the socioeconomic profiles data 
tract_data = tract_data.merge(sro_df_by_tract, how='left', left_on = 'Tract', right_on = 'tractce')
tract_data = tract_data.drop(['tractce'], axis=1).fillna(0)
tract_data.head()

### Rent-controlled

In [ ]:
# load the rent-controlled data
rc_df = pd.read_csv (r'./resources/rent_controlled_2019_for_NP.csv')
print(rc_df.columns)

In [ ]:
# aggregate the raw data into geographic units (neighborhood, census tract)
rc_df_by_neighborhood = rc_df.groupby("NHOOD").agg({'RESUNITS':['count','sum']})
rc_df_by_neighborhood.columns = ['rc_count', 'rc_residential_unit']
rc_df_by_neighborhood = rc_df_by_neighborhood.reset_index()

rc_df_by_tract = rc_df.groupby("tractce").agg({'RESUNITS':['count','sum']})
rc_df_by_tract.columns = ['rc_count', 'rc_residential_unit']
rc_df_by_tract = rc_df_by_tract.reset_index()

In [ ]:
# combine the data to the socioeconomic profiles data 
neigh_data = neigh_data.merge(rc_df_by_neighborhood, how= 'left', left_on = 'Neighborhood', right_on = 'NHOOD')
neigh_data= neigh_data.drop(['NHOOD'], axis=1)
neigh_data.head()

In [ ]:
# combine the data to the socioeconomic profiles data 
tract_data = tract_data.merge(rc_df_by_tract, how='left', left_on = 'Tract', right_on = 'tractce')
tract_data = tract_data.drop(['tractce'], axis=1).fillna(0)
tract_data.head()

## Eviction

Eviction data is derived from [xxxx dataset]() on DataSF(SF's open data portal). The code below adds number of eviction by categories as new attributes to the master data table. 

In [ ]:
#load the eviction data from DataSF: url = 'https://data.sfgov.org/resource/5cei-gny5.geojson'
url = "https://data.sfgov.org/resource/5cei-gny5.geojson?$limit=45000"
eviction = gpd.read_file(url)
print(eviction.columns)

In [ ]:
# drop the existing neighborhood column 
eviction = eviction.drop(['neighborhood'], axis=1)

In [ ]:
# run spatial join between neighborhood boundaries and pci street segment 

eviction_tract= eviction.sjoin(tract_df, how="left", predicate='intersects')
eviction_tract = pd.DataFrame(eviction_tract.drop(columns='geometry'))

eviction_neigh= eviction.sjoin(neigh_df, how="left", predicate='intersects')
eviction_neigh = pd.DataFrame(eviction_neigh.drop(columns='geometry'))

In [ ]:
# create a dictionary for aggregation 
eviction_keys = ['good_samaritan_ends','roommate_same_unit','illegal_use','lead_remediation','failure_to_sign_renewal','condo_conversion', 'nuisance',
       'access_denial','owner_move_in', 'demolition','substantial_rehab', 'late_payments','unapproved_subtenant','capital_improvement','breach', 'development','ellis_act_withdrawal', 'other_cause',
       'non_payment']
eviction_values = ['sum']*19
res = dict(zip(eviction_keys, eviction_values))

# aggregate the data by neighborhoods 
eviction_df_by_neighborhood = eviction_neigh.groupby("nhood").agg(res).astype(float)
eviction_df_by_neighborhood.columns = eviction_keys
eviction_df_by_neighborhood = eviction_df_by_neighborhood.reset_index()
eviction_df_by_neighborhood.head()

In [ ]:
# aggregate the data by tracts 
eviction_df_by_tract = eviction_tract.groupby("tractce").agg(res).astype(float)
eviction_df_by_tract.columns = eviction_keys
eviction_df_by_tract = eviction_df_by_tract.reset_index().convert_dtypes()
eviction_df_by_tract['tractce'] = eviction_df_by_tract['tractce'].astype(int)
eviction_df_by_tract.head()

In [ ]:
# add a row for SF 
eviction_df_sf = eviction_neigh.agg(res).astype(float)
#pd.Series(['sf'], index = ['neighborhood'])
eviction_df_sf = pd.Series(['sf'], index = ['nhood']).append(eviction_df_sf)
eviction_df_by_neighborhood = eviction_df_by_neighborhood.append(eviction_df_sf,ignore_index=True)
eviction_df_by_neighborhood.tail()

In [ ]:
# combine the data to the socioeconomic profiles data 
neigh_data = neigh_data.merge(eviction_df_by_neighborhood, how= 'left', left_on = 'Neighborhood', right_on = 'nhood')
neigh_data= neigh_data.drop(['nhood'], axis=1)
neigh_data.head()

In [ ]:
# combine the data to the socioeconomic profiles data 
tract_data = tract_data.merge(eviction_df_by_tract, how='left', left_on = 'Tract', right_on = 'tractce')
tract_data = tract_data.drop(['tractce'], axis=1).fillna(0)
tract_data.head()

## Equity Geographies/Project Boundaries

`np_boundaries.csv` file in thie repository contains data that shows whether various city-led projects and geographies for equitable development apply to the SF neighborhoods. The data is complied by city staff using GIS software in a way that each column in the file represent one equity geographies or project boundaries. The code below load and join the data to the master table. 


In [ ]:
# load the np_boundaries table 
np_boundaries = pd.read_csv (r'./resources/np_boundaries.csv')
np_boundaries_tract = np_boundaries.merge(geo_lookup_df, how='right', left_on='nhood', right_on = 'neighborhood')
np_boundaries.head()

In [ ]:
# join np_boundaries to the master table 

neigh_data = neigh_data.merge(np_boundaries, how= 'left', left_on = 'Neighborhood', right_on = 'nhood')
neigh_data= neigh_data.drop(['nhood'], axis=1)

neigh_data.head()


In [ ]:
# join np_boundaries to the master table 

tract_data = tract_data.merge(np_boundaries_tract, how='left', left_on = 'Tract', right_on = 'tractid')
tract_data = tract_data.drop(['tractid'], axis=1)

tract_data.head()

## Environmental Justice Area 

In [ ]:
# use your own ArcGIS Online credential for SF ArcGIS Online
gis = GIS("https://sfgov.maps.arcgis.com/", "seolha.lee_cpc", "25Minhaa!?!")
print(f"Connected to {gis.properties.portalHostname} as {gis.users.me.username}")


In [ ]:
# load the EJ area layer from SF ArcGIS Online 
# service directory: https://services.arcgis.com/Zs2aNLFN00jrS4gG/arcgis/rest/services/EJ_Communities/FeatureServer
ej_id = '496f54079f934da28c9fea605056d971'
ej = gis.content.get(ej_id)
ej

In [ ]:
# load the first layer of vz_2017 as 'layer'
ej_layer = ej.layers[0]
for f in ej_layer.properties.fields:
    print(f['name'])

In [ ]:
# export the features in the layer as a shapefile)
ej_layer.query(where = 'gridcode <999').sdf.spatial.to_featureclass('./resources/ej_communities.shp')

In [ ]:
# load the shapefile as a geopandas dataframe
ej_layer_shp = gpd.read_file('./resources/ej_communities.shp')
ej_layer_shp = ej_layer_shp.to_crs("EPSG:4326")

In [ ]:
# calculate the total length of Vision Zero by neighborhood
neigh_ej = neigh_df.sjoin(ej_layer_shp, how="right", predicate='intersects')
neigh_ej = pd.DataFrame(neigh_ej.drop(columns='geometry'))
neigh_ej['gridcode_wt'] = neigh_ej['gridcode']*neigh_ej['shape_area']


ej_mean_list = list()
ej_max_list = list()

for neighborhood in neighborhood_list: 
    sub_ej = neigh_ej[(neigh_ej["nhood"]==neighborhood)]
    
    ej_sum = sub_ej['gridcode_wt'].sum()
    area_sum = sub_ej['shape_area'].sum()
    ej_mean = ej_sum/area_sum
    ej_max = sub_ej['gridcode'].max()

    ej_mean_list.append(ej_mean)
    ej_max_list.append(ej_max)
    
    
neigh_ej_df = pd.DataFrame({'nhood': neighborhood_list, 'ej_mean':ej_mean_list, 'ej_max':ej_max_list})

In [ ]:
# calculate the total length of Vision Zero by neighborhood
tract_ej = tract_df.sjoin(ej_layer_shp, how="right", predicate='intersects')
tract_ej = pd.DataFrame(tract_ej.drop(columns='geometry'))
tract_ej['gridcode_wt'] = tract_ej['gridcode']*tract_ej['shape_area']


ej_mean_list = list()
ej_max_list = list()

for tract in tract_list:  
    sub_ej = tract_ej[(tract_ej["tractce"]==tract)]
    
    ej_sum = sub_ej['gridcode_wt'].sum()
    area_sum = sub_ej['shape_area'].sum()
    ej_mean = ej_sum/area_sum
    ej_max = sub_ej['gridcode'].max()

    ej_mean_list.append(ej_mean)
    ej_max_list.append(ej_max)
    
    
tract_ej_df = pd.DataFrame({'tractce': tract_list, 'ej_mean':ej_mean_list, 'ej_max':ej_max_list})

In [ ]:
# add the 'vz_length' as a column to the master table
neigh_data = neigh_data.merge(neigh_ej_df, how= 'left', left_on = 'Neighborhood', right_on = 'nhood')
neigh_data= neigh_data.drop(['nhood'], axis=1)

neigh_data.head()

In [ ]:
# add the 'vz_length' as a column to the master table
tract_data = tract_data.merge(tract_vz_df, how='left', left_on = 'Tract', right_on = 'tractce')
tract_data = tract_data.drop(['tractce'], axis=1)

tract_data.head()

## Built Environment

SFNP also provides indicators that summarises the qulity of built environment and the number of community amenities in the neighborhooods. The code below calcualtes three indicators, using datasets found on [DataSF] and SF Planning ArcGIS Online and the neighborhood boundaries shapefile in this repository. 

### Pavement Condition Index

In [ ]:
# load the PCI data from DataSF

url = "https://data.sfgov.org/resource/5aye-4rtt.geojson?$limit=45000"
pci = gpd.read_file(url)
pci['length'] = pci['geometry'].length

# filter items that has length > 0 (street segments)
pci = pci[pci['length'].notna()]
pci.dtypes

In [ ]:
# run spatial join between neighborhood boundaries and pci street segment 

neigh_pci = neigh_df.sjoin(pci, how="right", predicate='intersects')
neigh_pci = pd.DataFrame(neigh_pci.drop(columns='geometry'))

# calculate high_pci_ratio: high pci - PCI > 85 

high_pci_ratio = list()
for neighborhood in neighborhood_list: 
    total_len = neigh_pci['length'].sum()
    high_pci = neigh_pci[(neigh_pci["nhood"]==neighborhood) & (neigh_pci["pci_score"].astype(float)>85)]
    high_len = high_pci['length'].sum()
    high_pci_ratio.append(high_len/total_len)
        
        
high_pci_df_neigh = pd.DataFrame({'nhood': neighborhood_list, 'high_pci_ratio':high_pci_ratio})

In [ ]:
# run spatial join between neighborhood boundaries and pci street segment 

tract_pci = tract_df.sjoin(pci, how="right", predicate='intersects')
tract_pci = pd.DataFrame(tract_pci.drop(columns='geometry'))

# calculate high_pci_ratio: high pci - PCI > 85 

high_pci_ratio = list()
for tract in tract_list: 
    total_len = tract_pci['length'].sum()
    high_pci = tract_pci[(tract_pci["tractce"]==tract) & (tract_pci["pci_score"].astype(float)>85)]
    high_len = high_pci['length'].sum()
    high_pci_ratio.append(high_len/total_len)
        
        
high_pci_df_tract = pd.DataFrame({'tractce': tract_list, 'high_pci_ratio':high_pci_ratio}).convert_dtypes()
high_pci_df_tract['tractce'] = high_pci_df_tract['tractce'].astype(int)

In [ ]:
# add the 'high_pci_ratio' as a column to the master table

neigh_data = neigh_data.merge(high_pci_df_neigh, how= 'left', left_on = 'Neighborhood', right_on = 'nhood')
neigh_data= neigh_data.drop(['nhood'], axis=1)

neigh_data.head()

In [ ]:
# add the 'high_pci_ratio' as a column to the master table

tract_data = tract_data.merge(high_pci_df_tract, how='left', left_on = 'Tract', right_on = 'tractce')
tract_data = tract_data.drop(['tractce'], axis=1)

tract_data.head()

### Hign Injury Network

In [ ]:
# use your own ArcGIS Online credential for SF ArcGIS Online
gis = GIS("https://sfgov.maps.arcgis.com/", "seolha.lee_cpc", "25Minhaa!?!")
print(f"Connected to {gis.properties.portalHostname} as {gis.users.me.username}")


In [ ]:
# load the Vision Zero 2017 high injury network data from SF ArcGIS Online 
# service directory: https://services.arcgis.com/Zs2aNLFN00jrS4gG/arcgis/rest/services/vz_hin_2017_single_line/FeatureServer
vz_2017_id = '25d06501f18e458491ca7c6d4e3813b4'
vz_2017 = gis.content.get(vz_2017_id)
vz_2017

In [ ]:
# load the first layer of vz_2017 as 'layer'
layer = vz_2017.layers[0]
for f in layer.properties.fields:
    print(f['name'])

In [ ]:
# export the features in the layer as a shapefile
features = layer.query(where = 'length >0')
features.sdf.spatial.to_featureclass('./resources/vz_2017.shp')

In [ ]:
# load the shapefile as a geopandas dataframe
vz_2017_shp = gpd.read_file('./resources/vz_2017.shp')
vz_2017_shp = vz_2017_shp.to_crs("EPSG:4326")

# load the street centerline as a geopandas dataframe
st_ctl = gpd.read_file('./resources/Street_Centerline.shp').drop(['nhood'], axis=1)
st_ctl = st_ctl.to_crs("EPSG:4326")


In [ ]:
# calculate the total length of Vision Zero by neighborhood
neigh_vz_2017 = neigh_df.sjoin(vz_2017_shp, how="right", predicate='intersects')
neigh_vz_2017 = pd.DataFrame(neigh_vz_2017.drop(columns='geometry'))

neigh_st_ctl = neigh_df.sjoin(st_ctl, how='right', predicate='intersects')
neigh_st_ctl = pd.DataFrame(neigh_st_ctl.drop(columns='geometry'))
print(neigh_st_ctl.columns)

vz_length = list()
st_length = list()
vz_ratio_list = list()

for neighborhood in neighborhood_list: 
    sub_vz = neigh_vz_2017[(neigh_vz_2017["nhood"]==neighborhood)]
    sub_st = neigh_st_ctl[(neigh_st_ctl['nhood']==neighborhood)]
    total_vz_len = sub_vz['length'].sum()
    total_st_len = sub_st['st_length_'].sum()
    vz_ratio = total_vz_len/total_st_len
    
    vz_length.append(total_vz_len)
    st_length.append(total_st_len)
    vz_ratio_list.append(vz_ratio)
    
    
        
neigh_vz_df = pd.DataFrame({'nhood': neighborhood_list, 'vz_length':vz_length, 'st_length':st_length, 'vz_ratio':vz_ratio_list})

In [ ]:
# calculate the total length of Vision Zero by tract
tract_vz_2017 = tract_df.sjoin(vz_2017_shp, how="right", predicate='intersects')
tract_vz_2017 = pd.DataFrame(tract_vz_2017.drop(columns='geometry'))

tract_st_ctl = tract_df.sjoin(st_ctl, how='right', predicate='intersects')
tract_st_ctl = pd.DataFrame(tract_st_ctl.drop(columns='geometry'))
print(tract_st_ctl.columns)

vz_length = list()
st_length = list()
vz_ratio_list = list()

for tract in tract_list: 
    sub_vz = tract_vz_2017[(tract_vz_2017["tractce"]==tract)]
    sub_st = tract_st_ctl[(tract_st_ctl['tractce']==tract)]
    total_vz_len = sub_vz['length'].sum()
    total_st_len = sub_st['st_length_'].sum()
    vz_ratio = total_vz_len/total_st_len
    
    vz_length.append(total_vz_len)
    st_length.append(total_st_len)
    vz_ratio_list.append(vz_ratio)
    
tract_vz_df = pd.DataFrame({'tractce': tract_list, 'vz_length':vz_length, 'st_length':st_length, 'vz_ratio':vz_ratio_list}).convert_dtypes()
tract_vz_df['tractce'] = tract_vz_df['tractce'].astype(int)

In [ ]:
# add the 'vz_length' as a column to the master table
neigh_data = neigh_data.merge(neigh_vz_df, how= 'left', left_on = 'Neighborhood', right_on = 'nhood')
neigh_data= neigh_data.drop(['nhood'], axis=1)

neigh_data.head()

In [ ]:
# add the 'vz_length' as a column to the master table
tract_data = tract_data.merge(tract_vz_df, how='left', left_on = 'Tract', right_on = 'tractce')
tract_data = tract_data.drop(['tractce'], axis=1)

tract_data.head()

### Community Facilities

#### Rec and Park facilities

In [ ]:
# load the recreation and park facilities data from DataSF 
# https://data.sfgov.org/resource/gtr9-ntp6.geojson 
url = "https://data.sfgov.org/resource/gtr9-ntp6.geojson?$limit=45000"
rec = gpd.read_file(url)
rec = rec.to_crs("EPSG:4326")
rec.dtypes

In [ ]:
# join the neighborhood boundaries to the rec data 
neigh_rec = neigh_df.sjoin(rec[['objectid','propertytype', 'geometry']], how="right", predicate='intersects')
neigh_rec = pd.DataFrame(neigh_rec.drop(columns='geometry'))

propertytype_list = neigh_rec['propertytype'].unique()

# count the number of rec facilities in each neighborhood
rec_count = pd.DataFrame({'propertytype':propertytype_list})
for neighborhood in neighborhood_list: 
    sub = neigh_rec[(neigh_rec["nhood"]==neighborhood)].groupby('propertytype').agg({'nhood':'count'})
    sub.columns = [neighborhood]
    sub = sub.reset_index()
    rec_count = rec_count.merge(sub, on = 'propertytype', how='left') 

rec_count_neigh = rec_count.T.reset_index()
rec_count_neigh.columns = rec_count_neigh.iloc[0]
rec_count_neigh = rec_count_neigh[1:].rename(columns={'propertytype': 'Neighborhood'}).replace(np.nan, 0)
rec_count_neigh.head()

In [ ]:
# join the tract boundaries to the rec data 
tract_rec = tract_df.sjoin(rec[['objectid','propertytype', 'geometry']], how="right", predicate='intersects')
tract_rec = pd.DataFrame(tract_rec.drop(columns='geometry'))

propertytype_list = tract_rec['propertytype'].unique()

# count the number of rec facilities in each neighborhood
rec_count = pd.DataFrame({'propertytype':propertytype_list})
for tract in tract_list: 
    sub = tract_rec[(tract_rec["tractce"]==tract)].groupby('propertytype').agg({'tractce':'count'})
    sub.columns = [tract]
    sub = sub.reset_index()
    rec_count = rec_count.merge(sub, on = 'propertytype', how='left') 

rec_count_tract = rec_count.T.reset_index()
rec_count_tract.columns = rec_count_tract.iloc[0]
rec_count_tract = rec_count_tract[1:].rename(columns={'propertytype': 'Tract'}).replace(np.nan, 0)
rec_count_tract['Tract'] = rec_count_tract['Tract'].astype(int)
rec_count_tract.head()

In [ ]:
# add the 'vz_length' as a column to the master table
neigh_data = neigh_data.merge(rec_count_neigh, how= 'left', on = 'Neighborhood')
neigh_data.head()

In [ ]:
# add the 'vz_length' as a column to the master table
tract_data = tract_data.merge(rec_count_tract, how='left', on = 'Tract')
tract_data.head()

#### Schools

In [ ]:
# load the school data from DataSF as a geopandas point data
# https://data.sfgov.org/resource/gtr9-ntp6.geojson 
url = "https://data.sfgov.org/resource/rxa4-qmcf.json"

school = pd.read_json(url)
school_df = gpd.GeoDataFrame(school, geometry=gpd.points_from_xy(school.longitude, school.latitude, crs="EPSG:4326"))
school_df = school_df[school_df['common_name'].str.contains('High|Elementary|Middle')].reset_index(drop = True)
print(school_df.dtypes)
school_df.head()

In [ ]:
# spatial join the school point data to the neighborhood boundaries 
neigh_school = neigh_df.sjoin(school_df[['facility_id', 'common_name', 'geometry']], how="right", predicate='intersects')
neigh_school = pd.DataFrame(neigh_school.drop(columns='geometry'))
neigh_school.dtypes

tract_school = tract_df.sjoin(school_df[['facility_id', 'common_name', 'geometry']], how="right", predicate='intersects')
tract_school = pd.DataFrame(tract_school.drop(columns='geometry'))
tract_school.dtypes 

In [ ]:
# calculate the number of schools by neighborhood 
school_count_list = []
for neighborhood in neighborhood_list: 
    sub = neigh_school[(neigh_school["nhood"]==neighborhood)]
    school_count_list.append(len(sub))
    sub = sub.reset_index()
    
school_count_neigh = pd.DataFrame({'Neighborhood':neighborhood_list,
                               'school':school_count_list})
school_count_neigh.head()

In [ ]:
# calculate the number of schools by neighborhood 
school_count_list = []
for tract in tract_list: 
    sub = tract_school[(tract_school["tractce"]==tract)]
    school_count_list.append(len(sub))
    sub = sub.reset_index()
    
school_count_tract = pd.DataFrame({'Tract':tract_list,
                               'school':school_count_list}).convert_dtypes()
school_count_tract['Tract'] = school_count_tract['Tract'].astype(int)
school_count_tract.head()

In [ ]:
# add the 'school' as a column to the master table
neigh_data = neigh_data.merge(school_count_neigh, how= 'left', on = 'Neighborhood')
neigh_data.head()

In [ ]:
# add the 'school' as a column to the master table
tract_data = tract_data.merge(school_count_tract, how='left', on = 'Tract')
tract_data.head()

## Export the Master Tables

#### add nhood_url 
'nhood_url' will be used to build URLs of html tables. You can't use the original neighbohroods names in URLs because some of them contain '/' in it. Here we replace '/' with '-'. 

In [ ]:
# add nhood_url for neighborhood names for URLs. 
neigh_data['nhood_url'] = neigh_data['Neighborhood'].str.replace('/','-')

#### Export the master tables as csv files

In [ ]:
# export the neigh master table as csv 
neigh_data.to_csv(os.path.join(download_path,'Neighborhood_master_table_by_geo_{}_{}.csv'.format(year, year_past)), index = False)

# export only for the 'sf' row 
sf_data = neigh_data[neigh_data['Neighborhood']=='sf']
sf_data.to_csv(os.path.join(download_path,'SF_master_table_by_geo_{}_{}.csv'.format(year, year_past)), index = False)

# export the tract master table as csv 
tract_data.to_csv(os.path.join(download_path,'Tract_master_table_by_geo_{}_{}.csv'.format(year, year_past)), index = False)

#### Export the master layers as geojson files 
for SF_master_table_by_geo.csv, make the replacement below and upload the file manually on AGOL. Otherwise it gives an error in which the AGOL system recognizes the two columns as one column:
- Associate's --> Associate
- Bachelor's --> Bachelor

In [ ]:
# load the master tables 
neigh_data = pd.read_csv(os.path.join(download_path,'Neighborhood_master_table_by_geo_{}_{}.csv'.format(year, year_past)))
tract_data = pd.read_csv(os.path.join(download_path,'Tract_master_table_by_geo_{}_{}.csv'.format(year, year_past)))

# export the master tables as master layer geojson files 
# join dataframe to neighborhoods geodataframe by neighborhood name
neigh_data[neigh_data.select_dtypes(np.float64).columns] = neigh_data.select_dtypes(np.float64).astype(np.float32)
tract_data[tract_data.select_dtypes(np.float64).columns] = tract_data.select_dtypes(np.float64).astype(np.float32)


neigh_master_geo = neigh_df.merge(neigh_data,left_on='nhood', right_on='Neighborhood')
tract_master_geo = tract_df.merge(tract_data,left_on='tractce', right_on='Tract')

# export the geodataframes as geojson files 
neigh_master_geo.to_file(os.path.join(download_path,'Neighborhood_master_layer_{}.geojson'.format(year)), driver='GeoJSON')
tract_master_geo.to_file(os.path.join(download_path,'Tract_master_layer_{}.geojson'.format(year)), driver='GeoJSON')

## Publish Data to ArcGIS Online 

In [ ]:
import arcgis 
from arcgis.features import FeatureLayer
from arcgis.features import FeatureLayerCollection
from arcgis.gis import GIS

In [ ]:
# connect to SF ArcGIS Online using a valid credential
gis = GIS("https://sfgov.maps.arcgis.com/", "seolha.lee_cpc", "25Minhaa!?!")
print(f"Connected to {gis.properties.portalHostname} as {gis.users.me.username}")

In [ ]:
#load the master layer geojson files 
neigh_master_geo_path = os.path.join(download_path,'Neighborhood_master_layer_{}.geojson'.format(year))
tract_master_geo_path = os.path.join(download_path,'Tract_master_layer_{}.geojson'.format(year))

### Overwrite the existing layers

In [ ]:
search_result = gis.content.search('title:SFNP_master_neighborhood_2020', item_type='Feature Layer')
test_item = search_result[0]
test_feature_collection = FeatureLayerCollection.fromitem(test_item)
test_feature_collection.manager.overwrite(neigh_master_geo_path)

In [ ]:
search_result = gis.content.search('title:SFNP_master_tract_2020', item_type='Feature Layer')
test_item = search_result[0]
test_feature_collection = FeatureLayerCollection.fromitem(test_item)
test_feature_collection.manager.overwrite(tract_master_geo_path)

### Publish a new layer (only when there is no existing layer with the same name)

In [ ]:
#set the feature layer properties 
# neigh_prop = {"snippet":"""This feature layer is for San Francisco Planning Neighborhood Profiles (SFNP).""",
#                 "title":"SFNP_master_neighborhood_{}".format(year),
#                 "tags":"neighborhood profiles",
#                 "type":"GeoJson"}
# tract_prop = {"snippet":"""This feature layer is for San Francisco Planning Neighborhood Profiles (SFNP).""",
#                 "title":"SFNP_master_tract_{}".format(year),
#                 "tags":"neighborhood profiles",
#                 "type":"GeoJson"}


#publish the layers as feature layers to ArcGIS Online
# neigh_master_shp = gis.content.add(item_properties = neigh_prop, data = neigh_master_geo_path)
# tract_master_shp = gis.content.add(item_properties = tract_prop, data = tract_master_geo_path)

#neigh_master_shp.publish()
#tract_master_shp.publish()
